# Welcome to the Practical Exam :)
### <span style="color:purple"> **Please read the instructions, metadata and tips carefully in the practical exam PDF available on moodle!** </span>

**Also:**

-You can add as many cells as you like to answer the questions.

-You can make use of caching or persisting your RDDs or Dataframes, this may speed up performance.

**VERY IMPORTANT:** 

**- Don't forget to comment your code. Try to explain your reasoning to solve the exercises.**

**- Add your name to the .zip file submitted.**

**- Submit a .zip file. Files with other extensions will have a penalization.**

# PART A:

##  <span style="color:blue"> **0) Warmup (1 point):** </span>

#### a) Load the pages text file (pages.txt) into your DBFS:

In [0]:
#read the file 
pages = sc.textFile('dbfs:/FileStore/pages.txt')
pages.collect()

Out[284]: ['A -> B',
 'A -> C',
 'A -> D',
 'B -> D',
 'B -> A',
 'C -> D',
 'D -> E',
 'E -> D']

#### b) Using the Page Rank algorithm, which is the most popular page? (0.5):
##### Perform all the necessary transformations to the text file and implement the Page Rank algorithm in order to answer this question

In [0]:
#
def computeContribs(neighbors, rank):
  for neighbor in neighbors:
    yield(neighbor, rank/len(neighbors))

In [0]:
pages_neighbors = pages.map(lambda x: x.split(' -> ')).map(lambda y: (y[0],y[1])).distinct().groupByKey().persist()
pages_neighbors.collect()

Out[286]: [('C', <pyspark.resultiterable.ResultIterable at 0x7efce1bdfbe0>),
 ('A', <pyspark.resultiterable.ResultIterable at 0x7efce1b96b80>),
 ('B', <pyspark.resultiterable.ResultIterable at 0x7efce1b85100>),
 ('D', <pyspark.resultiterable.ResultIterable at 0x7efce1b85610>),
 ('E', <pyspark.resultiterable.ResultIterable at 0x7efce1b85bb0>)]

In [0]:
pages_ranks = pages_neighbors.map(lambda x: (x[0], 1.0))
pages_ranks.collect()

Out[287]: [('C', 1.0), ('A', 1.0), ('B', 1.0), ('D', 1.0), ('E', 1.0)]

In [0]:
for i in range(20):
  contributions = pages_neighbors.join(pages_ranks).flatMap(lambda x: computeContribs(x[1][0], x[1][1]))
  pages_ranks = contributions.reduceByKey(lambda rank1, rank2: rank1+rank2).map(lambda x: (x[0], x[1]*0.85+0.15))
  print(pages_ranks.collect())

[('D', 2.2533003877830766), ('A', 0.24301279014684984), ('C', 0.21885362387494078), ('B', 0.21885362387494078), ('E', 2.0659795743201905)]
[('E', 2.065305329615615), ('A', 0.24301279014684984), ('B', 0.21885362387494078), ('D', 2.2539746324876524), ('C', 0.21885362387494078)]
[('D', 2.253401524488763), ('A', 0.24301279014684984), ('C', 0.21885362387494078), ('E', 2.0658784376145043), ('B', 0.21885362387494078)]
[('A', 0.24301279014684984), ('C', 0.21885362387494078), ('D', 2.253888666287819), ('B', 0.21885362387494078), ('E', 2.0653912958154486)]
[('E', 2.0658053663446463), ('A', 0.24301279014684984), ('B', 0.21885362387494078), ('C', 0.21885362387494078), ('D', 2.2534745957586213)]
[('D', 2.2538265557084394), ('E', 2.065453406394828), ('B', 0.21885362387494078), ('C', 0.21885362387494078), ('A', 0.24301279014684984)]
[('A', 0.24301279014684984), ('B', 0.21885362387494078), ('D', 2.253527389751094), ('E', 2.0657525723521735), ('C', 0.21885362387494078)]
[('C', 0.21885362387494078), ('A

In [0]:
pages_ranks_c.sortBy(lambda pages: pages[1], ascending = False).collect()

Out[351]: [('D', 2.558333333333333),
 ('E', 1.0),
 ('A', 0.575),
 ('B', 0.43333333333333335),
 ('C', 0.43333333333333335)]

In [0]:
#D is the most popular!

#### C) Will ignoring C's contributions change these results? (0.5):
#### In other words, exclude C as a referencing page and repeat the algorithm. 

***Note that we do not intend to discard links that reference C, only the links where C is referencing other pages.***

In [0]:
pages_ranks_1 = pages_neighbors.map(lambda x: (x[0], 1.0))
pages_ranks_1.collect()

Out[291]: [('C', 1.0), ('A', 1.0), ('B', 1.0), ('D', 1.0), ('E', 1.0)]

In [0]:
pages_ranks_2=pages_ranks_1.filter(lambda x: x[0] != 'C')
pages_ranks_2.collect()

Out[292]: [('A', 1.0), ('B', 1.0), ('D', 1.0), ('E', 1.0)]

In [0]:
for i in range(20):
  contributions = pages_neighbors.join(pages_ranks_2).flatMap(lambda x: computeContribs(x[1][0], x[1][1]))
  pages_ranks_2 = contributions.reduceByKey(lambda rank1, rank2: rank1+rank2).map(lambda x: (x[0], x[1]*0.85+0.15))
  print(pages_ranks_2.collect())

[('B', 0.43333333333333335), ('A', 0.575), ('C', 0.43333333333333335), ('D', 1.708333333333333), ('E', 1.0)]
[('C', 0.3129166666666666), ('A', 0.33416666666666667), ('D', 1.7154166666666666), ('B', 0.3129166666666666), ('E', 1.6020833333333329)]
[('B', 0.24468055555555554), ('C', 0.24468055555555554), ('A', 0.2829895833333333), ('D', 2.0054201388888884), ('E', 1.6081041666666664)]
[('A', 0.2539892361111111), ('B', 0.2301803819444444), ('D', 1.909036631944444), ('C', 0.2301803819444444), ('E', 1.854607118055555)]
[('A', 0.24782666232638886), ('D', 2.0918596542245367), ('C', 0.22196361689814814), ('B', 0.22196361689814814), ('E', 1.7726811371527773)]
[('D', 2.0100001324508097), ('A', 0.24433453718171294), ('C', 0.22021755432581017), ('E', 1.928080706090856), ('B', 0.22021755432581017)]
[('B', 0.219228118868152), ('D', 2.138874100810787), ('E', 1.8585001125831881), ('C', 0.219228118868152), ('A', 0.2435924605884693)]
[('C', 0.21901786383339963), ('D', 2.078258811086003), ('A', 0.243171950

In [0]:
pages_ranks_2.sortBy(lambda pages: pages[1], ascending = False).collect()

Out[294]: [('D', 2.2287330375074665),
 ('E', 2.0517873920246004),
 ('A', 0.24301279063208753),
 ('C', 0.2188536243756648),
 ('B', 0.2188536243756648)]

##  <span style="color:blue"> **1) Data Load, Cleaning, and Feature Engineering (4 points):** </span>

#### a) Load the Online Retail file (onlineretail.csv) data into your DBFS:

In [0]:
retail = spark.read.csv("dbfs:/FileStore/onlineretail.csv", header="true", sep=",", inferSchema="true")
display(retail)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 536370 21883 STARS GIFT TAPE 24 12/1/2010 8:45 0.65 12583 France 536370 10002 INFLATABLE POLITICAL GLOBE 48 12/1/2010 8:45 0.85 12583 France 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 12/1/2010 8:45 1.25 12583 France 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 12/1/2010 8:45 2.95 12583 France 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 12/1/2010 8:45 2.95 12583 France 536370 22629 SPACEBOY LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22659 LUNCH BOX I LOVE LONDON 24 12/1/2010 8:45 1.95 12583 France 536370 22631 CIRCUS PARADE LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22661 CHARLOTTE BAG DOLLY GIRL DESIGN 20 12/1/2010 8:45 0.85 12583 France 536370 21731 RED TOADSTOOL LED NIGHT LIGHT 24 12/1/2010 8:45 1.65 12583 France 536370 22900 SET 2 TEA TOWELS I LOVE LONDON 24 12/1/2010 8:45 2.95 12583 France 536370 21913 VINTAGE SEASIDE JIGSAW PUZZLES 12 12/1/2010 8:45 3.75 12583 France 536370 22540 MINI JIGSAW CIRCUS PARADE 24 12/1/2010 8:45 0.42 12583 France 536370 22544 MINI JIGSAW SPACEBOY 24 12/1/2010 8:45 0.42 12583 France 536370 22492 MINI PAINT SET VINTAGE 36 12/1/2010 8:45 0.65 12583 France 536370 POST POSTAGE 3 12/1/2010 8:45 18.0 12583 France 536371 22086 PAPER CHAIN KIT 50'S CHRISTMAS 80 12/1/2010 9:00 2.55 13748 United Kingdom 536372 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 9:01 1.85 17850 United Kingdom 536372 22633 HAND WARMER UNION JACK 6 12/1/2010 9:01 1

#### b) Prepare the data for analysis (0.5):

##### For instance, load the data to a spark DataFrame, or create the necessary table in SparkSQL.

In [0]:
retail.createOrReplaceTempView("retailDF")
display(spark.sql("select * from retailDF"))

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 536370 21883 STARS GIFT TAPE 24 12/1/2010 8:45 0.65 12583 France 536370 10002 INFLATABLE POLITICAL GLOBE 48 12/1/2010 8:45 0.85 12583 France 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 12/1/2010 8:45 1.25 12583 France 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 12/1/2010 8:45 2.95 12583 France 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 12/1/2010 8:45 2.95 12583 France 536370 22629 SPACEBOY LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22659 LUNCH BOX I LOVE LONDON 24 12/1/2010 8:45 1.95 12583 France 536370 22631 CIRCUS PARADE LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22661 CHARLOTTE BAG DOLLY GIRL DESIGN 20 12/1/2010 8:45 0.85 12583 France 536370 21731 RED TOADSTOOL LED NIGHT LIGHT 24 12/1/2010 8:45 1.65 12583 France 536370 22900 SET 2 TEA TOWELS I LOVE LONDON 24 12/1/2010 8:45 2.95 12583 France 536370 21913 VINTAGE SEASIDE JIGSAW PUZZLES 12 12/1/2010 8:45 3.75 12583 France 536370 22540 MINI JIGSAW CIRCUS PARADE 24 12/1/2010 8:45 0.42 12583 France 536370 22544 MINI JIGSAW SPACEBOY 24 12/1/2010 8:45 0.42 12583 France 536370 22492 MINI PAINT SET VINTAGE 36 12/1/2010 8:45 0.65 12583 France 536370 POST POSTAGE 3 12/1/2010 8:45 18.0 12583 France 536371 22086 PAPER CHAIN KIT 50'S CHRISTMAS 80 12/1/2010 9:00 2.55 13748 United Kingdom 536372 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 9:01 1.85 17850 United Kingdom 536372 22633 HAND WARMER UNION JACK 6 12/1/2010 9:01 1

#### c) There are missing values in the columns CustomerID and Description. Discard all records that have null values in such columns (0.5):

In [0]:
display(spark.sql("select count (*) from retailDF"))

count(1) 541909

In [0]:
display(spark.sql("select count (*) from retailDF where CustomerID is null or Description is null"))


count(1) 135080

In [0]:
retailDF2=(spark.sql("select * from retailDF where CustomerID is not null and Description is not null"))
display(retailDF2)
retailDF2.createOrReplaceTempView("retailDF2")


InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 536370 21883 STARS GIFT TAPE 24 12/1/2010 8:45 0.65 12583 France 536370 10002 INFLATABLE POLITICAL GLOBE 48 12/1/2010 8:45 0.85 12583 France 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 12/1/2010 8:45 1.25 12583 France 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 12/1/2010 8:45 2.95 12583 France 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 12/1/2010 8:45 2.95 12583 France 536370 22629 SPACEBOY LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22659 LUNCH BOX I LOVE LONDON 24 12/1/2010 8:45 1.95 12583 France 536370 22631 CIRCUS PARADE LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22661 CHARLOTTE BAG DOLLY GIRL DESIGN 20 12/1/2010 8:45 0.85 12583 France 536370 21731 RED TOADSTOOL LED NIGHT LIGHT 24 12/1/2010 8:45 1.65 12583 France 536370 22900 SET 2 TEA TOWELS I LOVE LONDON 24 12/1/2010 8:45 2.95 12583 France 536370 21913 VINTAGE SEASIDE JIGSAW PUZZLES 12 12/1/2010 8:45 3.75 12583 France 536370 22540 MINI JIGSAW CIRCUS PARADE 24 12/1/2010 8:45 0.42 12583 France 536370 22544 MINI JIGSAW SPACEBOY 24 12/1/2010 8:45 0.42 12583 France 536370 22492 MINI PAINT SET VINTAGE 36 12/1/2010 8:45 0.65 12583 France 536370 POST POSTAGE 3 12/1/2010 8:45 18.0 12583 France 536371 22086 PAPER CHAIN KIT 50'S CHRISTMAS 80 12/1/2010 9:00 2.55 13748 United Kingdom 536372 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 9:01 1.85 17850 United Kingdom 536372 22633 HAND WARMER UNION JACK 6 12/1/2010 9:01 1

In [0]:
display(spark.sql("select count (*) from retailDF2 where CustomerID is null or Description is null"))

count(1) 0

In [0]:
display(spark.sql("select count (*) from retailDF2"))

count(1) 406829

#### d) Discard all the records in which Quantity has a negative number (1):

In [0]:
retailDF3=(spark.sql("select * from retailDF2 where Quantity >=0"))
display(retailDF3)
retailDF3.createOrReplaceTempView("retailDF3")


InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 536370 21883 STARS GIFT TAPE 24 12/1/2010 8:45 0.65 12583 France 536370 10002 INFLATABLE POLITICAL GLOBE 48 12/1/2010 8:45 0.85 12583 France 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 12/1/2010 8:45 1.25 12583 France 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 12/1/2010 8:45 2.95 12583 France 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 12/1/2010 8:45 2.95 12583 France 536370 22629 SPACEBOY LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22659 LUNCH BOX I LOVE LONDON 24 12/1/2010 8:45 1.95 12583 France 536370 22631 CIRCUS PARADE LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 536370 22661 CHARLOTTE BAG DOLLY GIRL DESIGN 20 12/1/2010 8:45 0.85 12583 France 536370 21731 RED TOADSTOOL LED NIGHT LIGHT 24 12/1/2010 8:45 1.65 12583 France 536370 22900 SET 2 TEA TOWELS I LOVE LONDON 24 12/1/2010 8:45 2.95 12583 France 536370 21913 VINTAGE SEASIDE JIGSAW PUZZLES 12 12/1/2010 8:45 3.75 12583 France 536370 22540 MINI JIGSAW CIRCUS PARADE 24 12/1/2010 8:45 0.42 12583 France 536370 22544 MINI JIGSAW SPACEBOY 24 12/1/2010 8:45 0.42 12583 France 536370 22492 MINI PAINT SET VINTAGE 36 12/1/2010 8:45 0.65 12583 France 536370 POST POSTAGE 3 12/1/2010 8:45 18.0 12583 France 536371 22086 PAPER CHAIN KIT 50'S CHRISTMAS 80 12/1/2010 9:00 2.55 13748 United Kingdom 536372 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 9:01 1.85 17850 United Kingdom 536372 22633 HAND WARMER UNION JACK 6 12/1/2010 9:01 1

In [0]:
display(spark.sql("select count (*) from retailDF3 where Quantity <0"))

count(1) 0

In [0]:
display(spark.sql("select count (*) from retailDF3"))

count(1) 397924

#### e) Create a new feature/column that corresponds to the amount spent (amount_spent) per record (1):
##### This can be done by computing amount_spent = quantity*unit_price.

In [0]:
retailDF4=(spark.sql("select * , round(Quantity*UnitPrice,2) as AmountSpent from retailDF3"))
retailDF4.createOrReplaceTempView("retailDF4")
display(retailDF4)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 15.3 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 22.0 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 15.3 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 25.5 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 11.1 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 11.1 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 54.08 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 12.6 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 12.6 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 30.0 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 9.9 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 25.5 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 19.9 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 17.85 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 17.85 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 31.8 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 31.8 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 25.5 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 17.85 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 90.0 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 90.0 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 45.0 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 10.2 536370 21883 STARS GIFT TAPE 24 12/1/2010 8:45 0.65 12583 France 15.6 536370 10002 INFLATABLE POLITICAL GLOBE 48 12/1/2010 8:45 0.85 12583 France 40.8 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 12/1/2010 8:45 1.25 12583 France 30.0 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 12/1/2010 8:45 2.95 12583 France 53.1 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 12/1/2010 8:45 2.95 12583 France 70.8 536370 22629 SPACEBOY LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 46.8 536370 22659 LUNCH BOX I LOVE LONDON 24 12/1/2010 8:45 1.95 12583 France 46.8 536370 22631 CIRCUS PARADE LUNCH BOX 24 12/1/2010 8:45 1.95 12583 France 46.8 536370 22661 CHARLOTTE BAG DOLLY GIRL DESIGN 20 12/1/2010 8:45 0.85 12583 France 17.0 536370 21731 RED TOADSTOOL LED NIGHT LIGHT 24 12/1/2010 8:45 1.65 12583 France 39.6 536370 22900 SET 2 TEA TOWELS I LOVE LONDON 24 12/1/2010 8:45 2.95 12583 France 70.8 536370 21913 VINTAGE SEASIDE JIGSAW PUZZLES 12 12/1/2010 8:45 3.75 12583 France 45.0 536370 22540 MINI JIGSAW CIRCUS PARADE 24 12/1/2010 8:45 0.42 12583 France 10.08 536370 22544 MINI JIGSAW SPACEBOY 24 12/1/2010 8:45 0.42 12583 France 10.08 536370 22492 MINI PAINT SET VINTAGE 36 12/1/2010 8:45 0.65 12583 France 23.4 536370 POST POSTAGE 3 12/1/201

#### f) Parse the invoice_date column and create one column for each of the following bits of information: year; month; day; hour. Then filter out all the invoices from 2011 (1):

In [0]:
retailDF4.dtypes

Out[304]: [('InvoiceNo', 'string'),
 ('StockCode', 'string'),
 ('Description', 'string'),
 ('Quantity', 'int'),
 ('InvoiceDate', 'string'),
 ('UnitPrice', 'double'),
 ('CustomerID', 'int'),
 ('Country', 'string'),
 ('AmountSpent', 'double')]

In [0]:
from pyspark.sql.functions import to_timestamp, month
from pyspark.sql import functions as F
spark.conf.set("spark.sql.legacy.timeParserPolicy","LEGACY")

retailDF5_1 = retailDF4.withColumn("dt_InvoiceDate", to_timestamp("InvoiceDate", "MM/dd/yyyy HH:mm"))
retailDF5_1.createOrReplaceTempView("retailDF5_1")
display(retailDF5_1)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 15.3 2010-12-01T08:26:00.000+0000 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 22.0 2010-12-01T08:26:00.000+0000 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 15.3 2010-12-01T08:26:00.000+0000 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 25.5 2010-12-01T08:26:00.000+0000 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 11.1 2010-12-01T08:28:00.000+0000 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 11.1 2010-12-01T08:28:00.000+0000 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 54.08 2010-12-01T08:34:00.000+0000 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 12.6 2010-12-01T08:34:00.000+0000 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 12.6 2010-12-01T08:34:00.000+0000 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 30.0 2010-12-01T08:34:00.000+0000 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 9.9 2010-12-01T08:34:00.000+0000 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 25.5 2010-12-01T08:34:00.000+0000 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 19.9 2010-12-01T08:34:00.000+0000 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 17.85 2010-12-01T08:34:00.000+0000 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 17.85 2010-12-01T08:34:00.000+0000 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 31.8 2010-12-01T08:34:00.000+0000 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 31.8 2010-12-01T08:34:00.000+0000 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 25.5 2010-12-01T08:34:00.000+0000 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 17.85 2010-12-01T08:35:00.000+0000 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 90.0 2010-12-01T08:45:00.000+0000 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 90.0 2010-12-01T08:45:00.000+0000 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 45.0 2010-12-01T08:45:00.000+0000 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 10.2 2010-12-01T08:45:00.000+0000 536370 21883 STARS GIFT TAPE 24 12/1/2010 8:45 0.65 12583 France 15.6 2010-12-01T08:45:00.000+0000 536370 10002 INFLATABLE POLITICAL GLOBE 48 12/1/2010 8:45 0.85 12583 France 40.8 2010-12-01T08:45:00.000+0000 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 12/1/2010 8:45 1.25 12583 France 30.0 2010-12-01T08:45:00.000+0000 536370 21035 SET/2 RED RETROSPOT TE

In [0]:
retailDF5_1.dtypes

Out[306]: [('InvoiceNo', 'string'),
 ('StockCode', 'string'),
 ('Description', 'string'),
 ('Quantity', 'int'),
 ('InvoiceDate', 'string'),
 ('UnitPrice', 'double'),
 ('CustomerID', 'int'),
 ('Country', 'string'),
 ('AmountSpent', 'double'),
 ('dt_InvoiceDate', 'timestamp')]

In [0]:
teste_1=(spark.sql("select * , year(dt_InvoiceDate) as year, month(dt_InvoiceDate) as month, dayofmonth(dt_InvoiceDate) as day, hour(dt_InvoiceDate) as hour   from retailDF5_1 where InvoiceDate in ('12/12/2010 16:14', '12/1/2010 8:26') "))
teste_1.createOrReplaceTempView("teste_1")
display(teste_1)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 15.3 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 22.0 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 15.3 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 25.5 2010-12-01T08:26:00.000+0000 2010 12 1 8 538518 90200C BLUE SWEETHEART BRACELET 1 12/12/2010 16:14 4.25 14505 United Kingdom 4.25 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22154 ANGEL DECORATION 3 BUTTONS 1 12/12/2010 16:14 0.42 14505 United Kingdom 0.42 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22900 SET 2 TEA TOWELS I LOVE LONDON 1 12/12/2010 16:14 2.95 14505 United Kingdom 2.95 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22713 CARD I LOVE LONDON 12 12/12/2010 16:14 0.42 14505 United Kingdom 5.04 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22659 LUNCH BOX I LOVE LONDON 1 12/12/2010 16:14 1.95 14505 United Kingdom 1.95 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 20828 GLITTER BUTTERFLY CLIPS 1 12/12/2010 16:14 2.55 14505 United Kingdom 2.55 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21820 GLITTER HEART GARLAND WITH BELLS 1 12/12/2010 16:14 3.75 14505 United Kingdom 3.75 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21809 CHRISTMAS HANGING TREE WITH BELL 4 12/12/2010 16:14 1.25 14505 United Kingdom 5.0 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 20663 QUEEN OF THE SKIES HOLIDAY PURSE 1 12/12/2010 16:14 2.95 14505 United Kingdom 2.95 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22758 LARGE PURPLE BABUSHKA NOTEBOOK 2 12/12/2010 16:14 1.25 14505 United Kingdom 2.5 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21014 SWISS CHALET TREE DECORATION 1 12/12/2010 16:14 0.85 14505 United Kingdom 0.85 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21647 ASSORTED TUTTI FRUTTI LARGE PURSE 1 12/12/2010 16:14 2.1 14505 United Kingdom 2.1 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21205 MULTICOLOUR 3D BALLS GARLAND 2 12/12/2010 16:14 2.55 14505 United Kingdom 5.1 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21201 TROPICAL HONEYCOMB PAPER GARLAND 3 12/12/2010 16:14 2.55 14505 United Kingdom 7.65 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22779 WOODEN OWLS LIGHT GARLAND 1 12/12/2010 16:14 4.25 14505 United Kingdom 4.25 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22469 HEART OF WICKER SMALL 1 12/12/2010 16:14 1.65 14505 United Kingdom 1.65 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 20713 JUMBO BAG OWLS 1 12/12/2010 16:14 1.95 14505 United Kingdom 1.95 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22752 SET 7 BABUSHKA NESTING BOXES 1 12/12/2010 16:14 8.5 14505 United Kingdom 8.5 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 84879 ASSORTED COLOUR BIRD ORNAMENT 8 12/12/2010 16:14 1.69 14505 United Kingdom 13.52 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 21815 STAR T-LIGHT HOLDER 4 12/12/2010 16:14 1.45 14505 United Kingdom 5.8 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22572 ROCKING HORSE GREEN CHRISTMAS 7 12/12/2010 16:14 0.85 14505 United Kingdom 5.95 2010-12-12T16:14:00.000+0000 2010 12 12 16 538518 22575 METAL MERRY CHRISTMAS WREATH 3 12/12/2010 16:14 1.95 14505 United Kingdom 5.85 2010-12-12T16:14:00.000+0000 2010 12 12 16 5

In [0]:

retailDF5_2=(spark.sql("select * , year(dt_InvoiceDate) as year, month(dt_InvoiceDate) as month, dayofmonth(dt_InvoiceDate) as day, hour(dt_InvoiceDate) as hour from retailDF5_1"))
retailDF5_2.createOrReplaceTempView("retailDF5_2")
display(retailDF5_2)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 12/1/2010 8:26 2.55 17850 United Kingdom 15.3 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 71053 WHITE METAL LANTERN 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 12/1/2010 8:26 2.75 17850 United Kingdom 22.0 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 12/1/2010 8:26 3.39 17850 United Kingdom 20.34 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 12/1/2010 8:26 7.65 17850 United Kingdom 15.3 2010-12-01T08:26:00.000+0000 2010 12 1 8 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 12/1/2010 8:26 4.25 17850 United Kingdom 25.5 2010-12-01T08:26:00.000+0000 2010 12 1 8 536366 22633 HAND WARMER UNION JACK 6 12/1/2010 8:28 1.85 17850 United Kingdom 11.1 2010-12-01T08:28:00.000+0000 2010 12 1 8 536366 22632 HAND WARMER RED POLKA DOT 6 12/1/2010 8:28 1.85 17850 United Kingdom 11.1 2010-12-01T08:28:00.000+0000 2010 12 1 8 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 12/1/2010 8:34 1.69 13047 United Kingdom 54.08 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 12/1/2010 8:34 2.1 13047 United Kingdom 12.6 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 12/1/2010 8:34 2.1 13047 United Kingdom 12.6 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 12/1/2010 8:34 3.75 13047 United Kingdom 30.0 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 22310 IVORY KNITTED MUG COSY 6 12/1/2010 8:34 1.65 13047 United Kingdom 9.9 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 12/1/2010 8:34 4.25 13047 United Kingdom 25.5 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 12/1/2010 8:34 9.95 13047 United Kingdom 19.9 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 21754 HOME BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 17.85 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 21755 LOVE BUILDING BLOCK WORD 3 12/1/2010 8:34 5.95 13047 United Kingdom 17.85 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 21777 RECIPE BOX WITH METAL HEART 4 12/1/2010 8:34 7.95 13047 United Kingdom 31.8 2010-12-01T08:34:00.000+0000 2010 12 1 8 536367 48187 DOORMAT NEW ENGLAND 4 12/1/2010 8:34 7.95 13047 United Kingdom 31.8 2010-12-01T08:34:00.000+0000 2010 12 1 8 536368 22960 JAM MAKING SET WITH JARS 6 12/1/2010 8:34 4.25 13047 United Kingdom 25.5 2010-12-01T08:34:00.000+0000 2010 12 1 8 536368 22913 RED COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 2010 12 1 8 536368 22912 YELLOW COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 2010 12 1 8 536368 22914 BLUE COAT RACK PARIS FASHION 3 12/1/2010 8:34 4.95 13047 United Kingdom 14.85 2010-12-01T08:34:00.000+0000 2010 12 1 8 536369 21756 BATH BUILDING BLOCK WORD 3 12/1/2010 8:35 5.95 13047 United Kingdom 17.85 2010-12-01T08:35:00.000+0000 2010 12 1 8 536370 22728 ALARM CLOCK BAKELIKE PINK 24 12/1/2010 8:45 3.75 12583 France 90.0 2010-12-01T08:45:00.000+0000 2010 12 1 8 536370 22727 ALARM CLOCK BAKELIKE RED 24 12/1/2010 8:45 3.75 12583 France 90.0 2010-12-01T08:45:00.000+0000 2010 12 1 8 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 12/1/2010 8:45 3.75 12583 France 45.0 2010-12-01T08:45:00.000+0000 2010 12 1 8 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 12/1/2010 8:45 0.85 12583 France 10.2 2010-12-01T08:45:00.00

In [0]:
teste_h=(spark.sql("select * from retailDF5_2 where dt_InvoiceDate is null"))
teste_h.createOrReplaceTempView("teste_h")
display(teste_h)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour

In [0]:
retailDF5=(spark.sql("select * from retailDF5_2 where year=2011"))
retailDF5.createOrReplaceTempView("retailDF5")
display(retailDF5)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour 539993 22386 JUMBO BAG PINK POLKADOT 10 1/4/2011 10:00 1.95 13313 United Kingdom 19.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 21499 BLUE POLKADOT WRAP 25 1/4/2011 10:00 0.42 13313 United Kingdom 10.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 21498 RED RETROSPOT WRAP 25 1/4/2011 10:00 0.42 13313 United Kingdom 10.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22379 RECYCLING BAG RETROSPOT 5 1/4/2011 10:00 2.1 13313 United Kingdom 10.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 20718 RED RETROSPOT SHOPPER BAG 10 1/4/2011 10:00 1.25 13313 United Kingdom 12.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 85099B JUMBO BAG RED RETROSPOT 10 1/4/2011 10:00 1.95 13313 United Kingdom 19.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 20682 RED RETROSPOT CHILDRENS UMBRELLA 6 1/4/2011 10:00 3.25 13313 United Kingdom 19.5 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22961 JAM MAKING SET PRINTED 12 1/4/2011 10:00 1.45 13313 United Kingdom 17.4 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22667 RECIPE BOX RETROSPOT 6 1/4/2011 10:00 2.95 13313 United Kingdom 17.7 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22898 CHILDRENS APRON APPLES DESIGN 8 1/4/2011 10:00 1.95 13313 United Kingdom 15.6 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22896 PEG BAG APPLES DESIGN 6 1/4/2011 10:00 2.55 13313 United Kingdom 15.3 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22303 COFFEE MUG APPLES DESIGN 6 1/4/2011 10:00 2.55 13313 United Kingdom 15.3 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22302 COFFEE MUG PEARS DESIGN 6 1/4/2011 10:00 2.55 13313 United Kingdom 15.3 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 85123A WHITE HANGING HEART T-LIGHT HOLDER 12 1/4/2011 10:00 2.95 13313 United Kingdom 35.4 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22808 SET OF 6 T-LIGHTS EASTER CHICKS 12 1/4/2011 10:00 2.95 13313 United Kingdom 35.4 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22458 CAST IRON HOOK GARDEN FORK 8 1/4/2011 10:00 2.55 13313 United Kingdom 20.4 2011-01-04T10:00:00.000+0000 2011 1 4 10 539993 22862 LOVE HEART NAPKIN BOX 4 1/4/2011 10:00 4.25 13313 United Kingdom 17.0 2011-01-04T10:00:00.000+0000 2011 1 4 10 540001 21733 RED HANGING HEART T-LIGHT HOLDER 32 1/4/2011 10:22 2.55 18097 United Kingdom 81.6 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 22062 CERAMIC BOWL WITH LOVE HEART DESIGN 24 1/4/2011 10:22 2.95 18097 United Kingdom 70.8 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 22060 LARGE CAKE STAND HANGING HEARTS 6 1/4/2011 10:22 9.95 18097 United Kingdom 59.7 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 22151 PLACE SETTING WHITE HEART 48 1/4/2011 10:22 0.42 18097 United Kingdom 20.16 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 22508 DOORSTOP RETROSPOT HEART 16 1/4/2011 10:22 3.39 18097 United Kingdom 54.24 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 21411 GINGHAM HEART DOORSTOP RED 12 1/4/2011 10:22 4.25 18097 United Kingdom 51.0 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 22644 CERAMIC CHERRY CAKE MONEY BANK 60 1/4/2011 10:22 1.45 18097 United Kingdom 87.0 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 70006 LOVE HEART POCKET WARMER 48 1/4/2011 10:22 0.42 18097 United Kingdom 20.16 2011-01-04T10:22:00.000+0000 2011 1 4 10 540001 21231 SWEETHEART CERAMIC TRINKET BOX 24 1/4/2011 10:22 1.25 18097 United Kingdom 30.0 2011-01-04T10:22:00.000+0000 2011 1 4 10 540002 21911 GARDEN METAL SIGN 12 1/4/2011 10:23 1.65 16656 United Kingdom 19.8 2011-01-04T10:23:00.000+0000 2011 1 4 10 540002 22625 RED KITCHEN SCALES 8 1/4/2011 10:23 8.5 16656 United Kingdom 68.0 2011-01-04T10:23:00.000+0000 2011 1 4 10 540002 21259 VICTORIAN SEWING BOX SMALL 24 1/4/2011 10:23 4.95 16656 United Kingdom 118.8 2011-01-04T10:23:00.000+0000 2011 1 4 10 540002 21790 VINTAGE SNAP CARDS 144 1/4/2011 10:23 0.72 16656 United Kingdom 103.68 2011-01-04T10:23:00.000+0000 2011 1 4 10 540003

## <span style="color:blue"> **2) Data Exploration (10 points):** </span>
### Using the ***data that you cleaned*** in the previous exercises, answer the following questions:

#### a) What are the top 5 customers with the highest number of orders? (1)
##### Remember that the same invoice number means one order even if it appears in many rows!

*Tip: if you opt for a query you might need to include the count of the number of distinct InvoiceNo!*

In [0]:
retailDF6=(spark.sql("select CustomerID, count(distinct(InvoiceNo)) as count_invoiceno from retailDF5 group by CustomerID order by 2 DESC limit 5"))
retailDF6.createOrReplaceTempView("retailDF6")
display(retailDF6)

CustomerID count_invoiceno 17841 7560 14911 5385 14096 5111 12748 3928 14606 2472

#### b) What are the top 5 customers with the highest money spent? (1)
##### Consider using the amount_spent column you created since it is an auxiliary column that multiplies the UnitPrice by the Quantity!

In [0]:
retailDF7=(spark.sql("select CustomerID, round(sum(AmountSpent),2) as TotalAmountSpent from retailDF5 group by CustomerID order by 2 DESC limit 5"))
retailDF7.createOrReplaceTempView("retailDF7")
display(retailDF7)

CustomerID TotalAmountSpent 14646 271614.14 18102 231822.69 17450 192521.95 16446 168472.5 14911 136087.12

#### c) What are the top 20 countries with the most orders? (1)
##### Same logic as in exercise 1, but instead of considering the customers we are considering the country.

In [0]:
retailDF8=(spark.sql("select Country, count(distinct(InvoiceNo)) as count_invoiceno from retailDF5 group by Country order by 2 DESC limit 20"))
retailDF8.createOrReplaceTempView("retailDF8")
display(retailDF8)

Country count_invoiceno United Kingdom 15358 Germany 427 France 368 EIRE 245 Belgium 93 Netherlands 92 Spain 86 Australia 54 Portugal 51 Switzerland 49 Finland 40 Italy 36 Sweden 34 Norway 34 Channel Islands 25 Poland 18 Denmark 17 Japan 16 Austria 16 Cyprus 15

#### d) What are the top 5 products that are purchased the most amount of times? (1)
##### Note that by most amount of times, we do NOT consider the quantity of the order, only the fact that that item was purchased.

In [0]:
#Understanding if there are multiple lines for the same product in the same invoice 
test1=(spark.sql("select InvoiceNo, StockCode, count(*) as count_StockCode from retailDF5 group by InvoiceNo, StockCode having count(*)>1 order by 1"))
test1.createOrReplaceTempView("test1")
display(test1)

InvoiceNo StockCode Description count_StockCode 540005 85062 PEARL CRYSTAL PUMPKIN T-LIGHT HLDR 2 540005 21034 REX CASH+CARRY JUMBO SHOPPER 2 540014 85194L HANGING SPRING FLOWER EGG LARGE 2 540021 21164 HOME SWEET HOME METAL SIGN 2 540023 22670 FRENCH WC SIGN BLUE METAL 2 540023 22315 200 RED + WHITE BENDY STRAWS 2 540023 21976 PACK OF 60 MUSHROOM CAKE CASES 2 540043 22112 CHOCOLATE HOT WATER BOTTLE 2 540093 79321 CHILLI LIGHTS 2 540093 21463 MIRRORED DISCO BALL 2 540093 22072 RED RETROSPOT TEA CUP AND SAUCER 2 540098 20727 LUNCH BAG BLACK SKULL. 2 540126 21110 LARGE CAKE TOWEL PINK SPOTS 2 540126 21109 LARGE CAKE TOWEL CHOCOLATE SPOTS 2 540146 22522 CHILDS GARDEN FORK BLUE 2 540168 22195 LARGE HEART MEASURING SPOONS 2 540172 85066 CREAM SWEETHEART MINI CHEST 2 540180 85123A WHITE HANGING HEART T-LIGHT HOLDER 2 540247 22956 36 FOIL HEART CAKE CASES 2 540247 84375 SET OF 20 KIDS COOKIE CUTTERS 2 540359 84997B RED 3 PIECE RETROSPOT CUTLERY SET 2 540359 84985A SET OF 72 GREEN PAPER DOILIES 2 540373 22312 OFFICE MUG WARMER POLKADOT 2 540373 21212 PACK OF 72 RETROSPOT CAKE CASES 2 540373 22352 LUNCH BOX WITH CUTLERY RETROSPOT 2 540373 22429 ENAMEL MEASURING JUG CREAM 2 540373 21533 RETROSPOT LARGE MILK JUG 2 540415 21034 REX CASH+CARRY JUMBO SHOPPER 2 540473 22811 SET OF 6 T-LIGHTS CACTI 2 540499 22624 IVORY KITCHEN SCALES 2 540499 22625 RED KITCHEN SCALES 2 540504 22804 CANDLEHOLDER PINK HANGING HEART 2 540506 21216 SET 3 RETROSPOT TEA,COFFEE,SUGAR 2 540506 22722 SET OF 6 SPICE TINS PANTRY DESIGN 2 540509 22440 BALLOON WATER BOMB PACK OF 35 2 540509 22631 CIRCUS PARADE LUNCH BOX 2 540511 22784 LANTERN CREAM GAZEBO 2 540511 22120 WELCOME WOODEN BLOCK LETTERS 2 540511 84879 ASSORTED COLOUR BIRD ORNAMENT 2 540511 21755 LOVE BUILDING BLOCK WORD 3 540512 22469 HEART OF WICKER SMALL 2 540514 22624 IVORY KITCHEN SCALES 2 540514 22625 RED KITCHEN SCALES 2 540514 22626 BLACK KITCHEN SCALES 2 540515 22413 METAL SIGN TAKE IT OR LEAVE IT 2 540516 22231 JIGSAW TREE WITH BIRDHOUSE 2 540516 84947 ANTIQUE SILVER TEA GLASS ENGRAVED 2 540520 21232 STRAWBERRY CERAMIC TRINKET BOX 2 540523 22241 GARLAND WOODEN HAPPY EASTER 2 540523 22333 RETROSPOT PARTY BAG + STICKER SET 2 540524 85071D CHARLIE+LOLA MY ROOM DOOR SIGN 2 540524 21326 AGED GLASS SILVER T-LIGHT HOLDER 3 540524 21161 KEEP OUT BOYS DOOR HANGER 2 540524 21756 BATH BUILDING BLOCK WORD 6 540524 85071C "CHARLIE+LOLA""EXTREMELY BUSY"" SIGN" 2 540524 84755 COLOUR GLASS T-LIGHT HOLDER HANGING 4 540524 22659 LUNCH BOX I LOVE LONDON 2 540528 21448 12 DAISY PEGS IN WOOD BOX 2 540538 47422 ASSORTED MONKEY SUCTION CUP HOOK 2 540543 85049G CHOCOLATE BOX RIBBONS 2 540545 84378 SET OF 3 HEART COOKIE CUTTERS 2 540545 84992 72 SWEETHEART FAIRY CAKE CASES 2 540545 22383 LUNCH BAG SUKI DESIGN 2 540545 22469 HEART OF WICKER SMALL 2 540545 22180 RETROSPOT LAMP 2 540566 35961 FOLKART ZINC HEART CHRISTMAS DEC 2 540566 21975 PACK OF 60 DINOSAUR CAKE CASES 2 540647 22937 BAKING MOULD CHOCOLATE CUPCAKES 2 540647 84947 ANTIQUE SILVER TEA GLASS ENGRAVED 2 540647 18098C PORCELAIN BUTTERFLY OIL BURNER 3 540647 37446 MINI CAKE STAND WITH HANGING CAKES 2 540647 72232 FENG SHUI PILLAR CANDLE 2 540647 22624 IVORY KITCHEN SCALES 2 540798 20992 JAZZ HEARTS PURSE NOTEBOOK 2 540798 22266 EASTER DECORATION HANGING BUNNY 2 540798 21027 NINJA RABBIT PINK 2 540798 47566 PARTY BUNTING 2 540803 21485 RETROSPOT HEART HOT WATER BOTTLE 2 540813 21481 FAWN BLUE HOT WATER BOTTLE 2 540813 22208 WOOD STAMP SET THANK YOU 2 540816 22659 LUNCH BOX I LOVE LONDON 2 540839 21123 SET/10 IVORY POLKADOT PARTY CANDLES 2 540839 21124 SET/10 BLUE POLKADOT PARTY CANDLES 2 540839 22284 HEN HOUSE DECORATION 2 540839 21126 SET OF 6 GIRLS CELEBRATION CANDLES 2 540839 22960 JAM MAKING SET WITH JARS 2 540940 85066 CREAM SWEETHEART MINI CHEST 2 540953 22367 CHILDRENS APRON SPACEBOY DESIGN 2 540953 21156 RETROSPOT CHILDRENS APRON 2 540953 84375 SET OF 20 KIDS COOKIE CUTTERS 2 540953 84992 72 SWEETHEART FAIRY CAKE CASES 2 540953 21212 PACK OF 72 RETROSPOT CAKE C

In [0]:
test=(spark.sql("select * from retailDF5 where InvoiceNo=536409 AND StockCode='90199C' order by StockCode"))
test.createOrReplaceTempView("test")
display(test)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour

In [0]:
#Top5 with distinct count
retailDF9=(spark.sql("select Description, StockCode, count(distinct(InvoiceNo)) as count_invoiceno from retailDF5 group by Description, StockCode order by 3 DESC limit 5"))
retailDF9.createOrReplaceTempView("retailDF9")
display(retailDF9)

Description StockCode count_invoiceno WHITE HANGING HEART T-LIGHT HOLDER 85123A 1770 REGENCY CAKESTAND 3 TIER 22423 1566 JUMBO BAG RED RETROSPOT 85099B 1517 PARTY BUNTING 47566 1357 ASSORTED COLOUR BIRD ORNAMENT 84879 1284

In [0]:
#Top5 without distinct count - includes duplication factor of multiple lines with the same product in the same invoice, so we obtain different results
retailDF9_1=(spark.sql("select Description, StockCode, count(InvoiceNo) as count_invoiceno from retailDF5 group by Description, StockCode order by 3 DESC limit 5"))
retailDF9_1.createOrReplaceTempView("retailDF9_1")
display(retailDF9_1)

Description StockCode count_invoiceno WHITE HANGING HEART T-LIGHT HOLDER 85123A 1821 REGENCY CAKESTAND 3 TIER 22423 1583 JUMBO BAG RED RETROSPOT 85099B 1534 PARTY BUNTING 47566 1374 ASSORTED COLOUR BIRD ORNAMENT 84879 1314

#### e)  What is the name (Description) of the most expensive item? (3)

In [0]:
#Top5 with distinct count
retailDF10=(spark.sql("select * from retailDF5 order by 2 DESC limit 10"))
retailDF10.createOrReplaceTempView("retailDF10")
display(retailDF10)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour 580153 POST POSTAGE 5 12/2/2011 10:23 28.0 12762 Portugal 140.0 2011-12-02T10:23:00.000+0000 2011 12 2 10 580154 POST POSTAGE 1 12/2/2011 10:24 18.0 12569 Germany 18.0 2011-12-02T10:24:00.000+0000 2011 12 2 10 580281 POST POSTAGE 1 12/2/2011 13:15 40.0 12704 Finland 40.0 2011-12-02T13:15:00.000+0000 2011 12 2 13 580160 POST POSTAGE 7 12/2/2011 10:47 18.0 12700 France 126.0 2011-12-02T10:47:00.000+0000 2011 12 2 10 580120 POST POSTAGE 1 12/1/2011 16:38 18.0 12553 France 18.0 2011-12-01T16:38:00.000+0000 2011 12 1 16 580144 POST POSTAGE 1 12/2/2011 9:53 18.0 12684 France 18.0 2011-12-02T09:53:00.000+0000 2011 12 2 9 580123 POST POSTAGE 2 12/1/2011 17:07 40.0 12664 Finland 80.0 2011-12-01T17:07:00.000+0000 2011 12 1 17 580126 POST POSTAGE 3 12/1/2011 17:20 18.0 12562 France 54.0 2011-12-01T17:20:00.000+0000 2011 12 1 17 580265 POST POSTAGE 1 12/2/2011 12:47 40.0 12587 Finland 40.0 2011-12-02T12:47:00.000+0000 2011 12 2 12 580152 POST POSTAGE 1 12/2/2011 10:22 15.0 12364 Belgium 15.0 2011-12-02T10:22:00.000+0000 2011 12 2 10

In [0]:
#Top5 with distinct count
retailDF10=(spark.sql("select Description, max(UnitPrice) from retailDF5 group by Description order by 2 DESC limit 1"))
retailDF10.createOrReplaceTempView("retailDF10")
display(retailDF10)

Description max(UnitPrice) POSTAGE 8142.75

In [0]:
test2=(spark.sql("select * from retailDF5 where Description='POSTAGE'"))
test2.createOrReplaceTempView("test2")
display(test2)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country AmountSpent dt_InvoiceDate year month day hour 540040 POST POSTAGE 5 1/4/2011 14:20 40.0 12483 Sweden 200.0 2011-01-04T14:20:00.000+0000 2011 1 4 14 540178 POST POSTAGE 3 1/5/2011 12:42 18.0 12681 France 54.0 2011-01-05T12:42:00.000+0000 2011 1 5 12 540239 POST POSTAGE 4 1/5/2011 14:48 18.0 12682 France 72.0 2011-01-05T14:48:00.000+0000 2011 1 5 14 540351 POST POSTAGE 2 1/6/2011 14:26 18.0 12735 France 36.0 2011-01-06T14:26:00.000+0000 2011 1 6 14 540365 POST POSTAGE 3 1/6/2011 16:12 18.0 12413 France 54.0 2011-01-06T16:12:00.000+0000 2011 1 6 16 540410 POST POSTAGE 3 1/7/2011 10:04 18.0 12530 Germany 54.0 2011-01-07T10:04:00.000+0000 2011 1 7 10 540414 POST POSTAGE 3 1/7/2011 10:32 18.0 12481 Germany 54.0 2011-01-07T10:32:00.000+0000 2011 1 7 10 540455 POST POSTAGE 3 1/7/2011 12:07 18.0 12583 France 54.0 2011-01-07T12:07:00.000+0000 2011 1 7 12 540458 POST POSTAGE 8 1/7/2011 12:28 18.0 12501 Germany 144.0 2011-01-07T12:28:00.000+0000 2011 1 7 12 540463 POST POSTAGE 2 1/7/2011 13:13 18.0 12489 France 36.0 2011-01-07T13:13:00.000+0000 2011 1 7 13 540469 POST POSTAGE 4 1/7/2011 14:04 28.0 12484 Spain 112.0 2011-01-07T14:04:00.000+0000 2011 1 7 14 540480 POST POSTAGE 4 1/7/2011 15:27 18.0 12480 Germany 72.0 2011-01-07T15:27:00.000+0000 2011 1 7 15 540519 POST POSTAGE 2 1/9/2011 12:12 28.0 12793 Portugal 56.0 2011-01-09T12:12:00.000+0000 2011 1 9 12 540546 POST POSTAGE 3 1/9/2011 15:56 28.0 12766 Portugal 84.0 2011-01-09T15:56:00.000+0000 2011 1 9 15 540553 POST POSTAGE 1 1/10/2011 9:48 18.0 12500 Germany 18.0 2011-01-10T09:48:00.000+0000 2011 1 10 9 540562 POST POSTAGE 3 1/10/2011 10:35 18.0 12524 Germany 54.0 2011-01-10T10:35:00.000+0000 2011 1 10 10 540642 POST POSTAGE 7 1/10/2011 13:22 18.0 12681 France 126.0 2011-01-10T13:22:00.000+0000 2011 1 10 13 540688 POST POSTAGE 5 1/11/2011 7:57 18.0 12736 France 90.0 2011-01-11T07:57:00.000+0000 2011 1 11 7 540769 POST POSTAGE 1 1/11/2011 10:38 18.0 12601 Germany 18.0 2011-01-11T10:38:00.000+0000 2011 1 11 10 540789 POST POSTAGE 2 1/11/2011 11:48 18.0 12643 France 36.0 2011-01-11T11:48:00.000+0000 2011 1 11 11 540801 POST POSTAGE 6 1/11/2011 12:25 28.0 12540 Spain 168.0 2011-01-11T12:25:00.000+0000 2011 1 11 12 540824 POST POSTAGE 2 1/11/2011 13:31 18.0 12728 France 36.0 2011-01-11T13:31:00.000+0000 2011 1 11 13 540835 POST POSTAGE 1 1/11/2011 15:00 18.0 12724 France 18.0 2011-01-11T15:00:00.000+0000 2011 1 11 15 540900 POST POSTAGE 2 1/12/2011 11:46 18.0 12712 Germany 36.0 2011-01-12T11:46:00.000+0000 2011 1 12 11 540971 POST POSTAGE 4 1/12/2011 14:10 15.0 12383 Belgium 60.0 2011-01-12T14:10:00.000+0000 2011 1 12 14 540972 POST POSTAGE 3 1/12/2011 14:13 18.0 12437 France 54.0 2011-01-12T14:13:00.000+0000 2011 1 12 14 540976 POST POSTAGE 7 1/12/2011 15:00 18.0 12652 France 126.0 2011-01-12T15:00:00.000+0000 2011 1 12 15 541093 POST POSTAGE 5 1/13/2011 13:21 18.0 12471 Germany 90.0 2011-01-13T13:21:00.000+0000 2011 1 13 13 541115 POST POSTAGE 7 1/13/2011 15:34 28.0 12578 Italy 196.0 2011-01-13T15:34:00.000+0000 2011 1 13 15 541120 POST POSTAGE 5 1/14/2011 9:13 18.0 12490 France 90.0 2011-01-14T09:13:00.000+0000 2011 1 14 9 541122 POST POSTAGE 2 1/14/2011 9:23 18.0 12708 Germany 36.0 2011-01-14T09:23:00.000+0000 2011 1 14 9 541125 POST POSTAGE 1 1/14/2011 10:06 18.0 12474 Germany 18.0 2011-01-14T10:06:00.000+0000 2011 1 14 10 541138 POST POSTAGE 6 1/14/2011 10:42 18.0 12553 France 108.0 2011-01-14T10:42:00.000+0000 2011 1 14 10 541224 POST POSTAGE 1 1/14/2011 14:45 18.0 12474 Germany 18.0 2011-01-14T14:45:00.000+0000 2011 1 14 14 541269 POST POSTAGE 8 1/17/2011 11:01 18.0 12626 Germany 144.0 2011-01-17T11:01:00.000+0000 2011 1 17 11 541405 POST POSTAGE 5 1/17/2011 15:17 18.0 12683 France 90.0 2011-01-17T15:17:00.000+0000 2011 1 17 15 541430 POST POSTAGE 18 1/18/2011 9:50 18.0 12356 Portugal 324.0 2011-01-18T09:50:00.000+0000 2011 1 18 9 541480 POST POSTAGE 1 1/18/2011 12:05 18.0 12527 Germany 18.0 2011-01-

#### f) What are the top ten most popular words in the Description column? (3)

##### This is a word count exercise.
*Tip: you can use `.rdd` to convert a dataframe to an RDD. This will be an RDD of row objects. Make sure your top 5 words are actually words, you may have to remove empty strings!*

In [0]:
#we are selecting the column Description from our dataframe 
#Then transforming it to an rdd so we can after combine all the values 
#then we are using the funtion flatmap to effectivelu combining it into a list all the word we found on the data frame 
Description_list=retailDF5.select('Description').rdd.flatMap(lambda x: x) 
Description_list.collect()

Out[321]: ['JUMBO BAG PINK POLKADOT',
 'BLUE POLKADOT WRAP',
 'RED RETROSPOT WRAP ',
 'RECYCLING BAG RETROSPOT ',
 'RED RETROSPOT SHOPPER BAG',
 'JUMBO BAG RED RETROSPOT',
 'RED RETROSPOT CHILDRENS UMBRELLA',
 'JAM MAKING SET PRINTED',
 'RECIPE BOX RETROSPOT ',
 'CHILDRENS APRON APPLES DESIGN',
 'PEG BAG APPLES DESIGN',
 'COFFEE MUG APPLES DESIGN',
 'COFFEE MUG PEARS  DESIGN',
 'WHITE HANGING HEART T-LIGHT HOLDER',
 'SET OF 6 T-LIGHTS EASTER CHICKS',
 'CAST IRON HOOK GARDEN FORK',
 'LOVE HEART NAPKIN BOX ',
 'RED HANGING HEART T-LIGHT HOLDER',
 'CERAMIC BOWL WITH LOVE HEART DESIGN',
 'LARGE CAKE STAND HANGING HEARTS',
 'PLACE SETTING WHITE HEART',
 'DOORSTOP RETROSPOT HEART',
 'GINGHAM HEART  DOORSTOP RED',
 'CERAMIC CHERRY CAKE MONEY BANK',
 'LOVE HEART POCKET WARMER',
 'SWEETHEART CERAMIC TRINKET BOX',
 'GARDEN METAL SIGN ',
 'RED KITCHEN SCALES',
 'VICTORIAN SEWING BOX SMALL ',
 'VINTAGE SNAP CARDS',
 'HANGING HEART ZINC T-LIGHT HOLDER',
 'BREAD BIN DINER STYLE RED ',
 'IVORY KITCHE

In [0]:
#counting how many values - rows we have 
Description_list.count()

Out[322]: 371764

In [0]:
# Verifying if the function does what we want: Seperate all the 'rows' by space, so we have each word seperated
Description_list.flatMap(lambda x:x.split()).collect()

Out[323]: ['JUMBO',
 'BAG',
 'PINK',
 'POLKADOT',
 'BLUE',
 'POLKADOT',
 'WRAP',
 'RED',
 'RETROSPOT',
 'WRAP',
 'RECYCLING',
 'BAG',
 'RETROSPOT',
 'RED',
 'RETROSPOT',
 'SHOPPER',
 'BAG',
 'JUMBO',
 'BAG',
 'RED',
 'RETROSPOT',
 'RED',
 'RETROSPOT',
 'CHILDRENS',
 'UMBRELLA',
 'JAM',
 'MAKING',
 'SET',
 'PRINTED',
 'RECIPE',
 'BOX',
 'RETROSPOT',
 'CHILDRENS',
 'APRON',
 'APPLES',
 'DESIGN',
 'PEG',
 'BAG',
 'APPLES',
 'DESIGN',
 'COFFEE',
 'MUG',
 'APPLES',
 'DESIGN',
 'COFFEE',
 'MUG',
 'PEARS',
 'DESIGN',
 'WHITE',
 'HANGING',
 'HEART',
 'T-LIGHT',
 'HOLDER',
 'SET',
 'OF',
 '6',
 'T-LIGHTS',
 'EASTER',
 'CHICKS',
 'CAST',
 'IRON',
 'HOOK',
 'GARDEN',
 'FORK',
 'LOVE',
 'HEART',
 'NAPKIN',
 'BOX',
 'RED',
 'HANGING',
 'HEART',
 'T-LIGHT',
 'HOLDER',
 'CERAMIC',
 'BOWL',
 'WITH',
 'LOVE',
 'HEART',
 'DESIGN',
 'LARGE',
 'CAKE',
 'STAND',
 'HANGING',
 'HEARTS',
 'PLACE',
 'SETTING',
 'WHITE',
 'HEART',
 'DOORSTOP',
 'RETROSPOT',
 'HEART',
 'GINGHAM',
 'HEART',
 'DOORSTOP',
 'RED',
 

In [0]:
#flatMap(lambda x:x.split()) - split each value of the index by space, i.e. having a list of words
#map(lambda word: (word, 1)) - giving each word the value 1
#reduceByKey(lambda word1,word2:word1+word2) - summing the values by each word
#sortBy(lambda word: -word[1] - ordering the new list of tuples by the value of the count in descending order 

Description_Words = Description_list.flatMap(lambda x:x.split()).map(lambda word: (word, 1)).reduceByKey(lambda word1,word2:word1+word2).sortBy(lambda word: -word[1])

#gives the first 10 
Description_Words.take(10)

Out[324]: [('OF', 38886),
 ('SET', 38731),
 ('BAG', 36242),
 ('RED', 29496),
 ('HEART', 27020),
 ('VINTAGE', 24431),
 ('RETROSPOT', 24428),
 ('DESIGN', 22185),
 ('PINK', 18868),
 ('CHRISTMAS', 17460)]

# PART B:

## <span style="color:blue"> **Machine Learning (3 points):** </span>

#### a) Load the insurance dataset and perform the following operations: (0.5)
##### - Filter out (remove from the dataset) the region column.
##### - Encode the values in the smoker column in the following manner:
1. If the person is a smoker his/her value in this column should be 1
2. If the person is not a smoker his/her value in this column should be 0

In [0]:
insurance_original = spark.read.csv("dbfs:/FileStore/insurance.csv", header="true", sep=",", inferSchema="true")
display(insurance_original)

age sex bmi children smoker region charges 19 female 27.9 0 yes southwest 16884.924 18 male 33.77 1 no southeast 1725.5523 28 male 33.0 3 no southeast 4449.462 33 male 22.705 0 no northwest 21984.47061 32 male 28.88 0 no northwest 3866.8552 31 female 25.74 0 no southeast 3756.6216 46 female 33.44 1 no southeast 8240.5896 37 female 27.74 3 no northwest 7281.5056 37 male 29.83 2 no northeast 6406.4107 60 female 25.84 0 no northwest 28923.13692 25 male 26.22 0 no northeast 2721.3208 62 female 26.29 0 yes southeast 27808.7251 23 male 34.4 0 no southwest 1826.843 56 female 39.82 0 no southeast 11090.7178 27 male 42.13 0 yes southeast 39611.7577 19 male 24.6 1 no southwest 1837.237 52 female 30.78 1 no northeast 10797.3362 23 male 23.845 0 no northeast 2395.17155 56 male 40.3 0 no southwest 10602.385 30 male 35.3 0 yes southwest 36837.467 60 female 36.005 0 no northeast 13228.84695 30 female 32.4 1 no southwest 4149.736 18 male 34.1 0 no southeast 1137.011 34 female 31.92 1 yes northeast 37701.8768 37 male 28.025 2 no northwest 6203.90175 59 female 27.72 3 no southeast 14001.1338 63 female 23.085 0 no northeast 14451.83515 55 female 32.775 2 no northwest 12268.63225 23 male 17.385 1 no northwest 2775.19215 31 male 36.3 2 yes southwest 38711.0 22 male 35.6 0 yes southwest 35585.576 18 female 26.315 0 no northeast 2198.18985 19 female 28.6 5 no southwest 4687.797 63 male 28.31 0 no northwest 13770.0979 28 male 36.4 1 yes southwest 51194.55914 19 male 20.425 0 no northwest 1625.43375 62 female 32.965 3 no northwest 15612.19335 26 male 20.8 0 no southwest 2302.3 35 male 36.67 1 yes northeast 39774.2763 60 male 39.9 0 yes southwest 48173.361 24 female 26.6 0 no northeast 3046.062 31 female 36.63 2 no southeast 4949.7587 41 male 21.78 1 no southeast 6272.4772 37 female 30.8 2 no southeast 6313.759 38 male 37.05 1 no northeast 6079.6715 55 male 37.3 0 no southwest 20630.28351 18 female 38.665 2 no northeast 3393.35635 28 female 34.77 0 no northwest 3556.9223 60 female 24.53 0 no southeast 12629.8967 36 male 35.2 1 yes southeast 38709.176 18 female 35.625 0 no northeast 2211.13075 21 female 33.63 2 no northwest 3579.8287 48 male 28.0 1 yes southwest 23568.272 36 male 34.43 0 yes southeast 37742.5757 40 female 28.69 3 no northwest 8059.6791 58 male 36.955 2 yes northwest 47496.49445 58 female 31.825 2 no northeast 13607.36875 18 male 31.68 2 yes southeast 34303.1672 53 female 22.88 1 yes southeast 23244.7902 34 female 37.335 2 no northwest 5989.52365 43 male 27.36 3 no northeast 8606.2174 25 male 33.66 4 no southeast 4504.6624 64 male 24.7 1 no northwest 30166.61817 28 female 25.935 1 no northwest 4133.64165 20 female 22.42 0 yes northwest 14711.7438 19 female 28.9 0 no southwest 1743.214 61 female 39.1 2 no southwest 14235.072 40 male 26.315 1 no northwest 6389.37785 40 female 36.19 0 no southeast 5920.1041 28 male 23.98 3 yes southeast 17663.1442 27 female 24.75 0 yes southeast 16577.7795 31 male 28.5 5 no northeast 6799.458 53 female 28.1 3 no southwest 11741.726 58 male 32.01 1 no southeast 11946.6259 44 male 27.4 2 no southwest 7726.854 57 male 34.01 0 no northwest 11356.6609 29 female 29.59 1 no southeast 3947.4131 21 male 35.53 0 no southeast 1532.4697 22 female 39.805 0 no northeast 2755.02095 41 female 32.965 0 no northwest 6571.02435 31 male 26.885 1 no northeast 4441.21315 45 female 38.285 0 no northeast 7935.29115 22 male 37.62 1 yes southeast 37165.1638 48 female 41.23 4 no northwest 11033.6617 37 female 34.8 2 yes southwest 39836.519 45 male 22.895 2 yes northwest 21098.55405 57 female 31.16 0 yes northwest 43578.9394 56 female 27.2 0 no southwest 11073.176 46 female 27.74 0 no northwest 8026.6666 55 female 26.98 0 no northwest 11082.5772 21 female 39.49 0 no southeast 2026.9741 53 female 24.795 1 no northwest 10942.13205 59 male 29.83 3 yes northeast 30184.9367 35 male 34.77 2 no northwest 5729.0053 64 female 31.3 2 yes southwest 47291.055 28 female 37.62 1 no southeast 3766.8838 54 female 30.8 3 no southwest 12105.32 55 male 

In [0]:
insurance=insurance_original.drop("region")
display(insurance)

age sex bmi children smoker charges 19 female 27.9 0 yes 16884.924 18 male 33.77 1 no 1725.5523 28 male 33.0 3 no 4449.462 33 male 22.705 0 no 21984.47061 32 male 28.88 0 no 3866.8552 31 female 25.74 0 no 3756.6216 46 female 33.44 1 no 8240.5896 37 female 27.74 3 no 7281.5056 37 male 29.83 2 no 6406.4107 60 female 25.84 0 no 28923.13692 25 male 26.22 0 no 2721.3208 62 female 26.29 0 yes 27808.7251 23 male 34.4 0 no 1826.843 56 female 39.82 0 no 11090.7178 27 male 42.13 0 yes 39611.7577 19 male 24.6 1 no 1837.237 52 female 30.78 1 no 10797.3362 23 male 23.845 0 no 2395.17155 56 male 40.3 0 no 10602.385 30 male 35.3 0 yes 36837.467 60 female 36.005 0 no 13228.84695 30 female 32.4 1 no 4149.736 18 male 34.1 0 no 1137.011 34 female 31.92 1 yes 37701.8768 37 male 28.025 2 no 6203.90175 59 female 27.72 3 no 14001.1338 63 female 23.085 0 no 14451.83515 55 female 32.775 2 no 12268.63225 23 male 17.385 1 no 2775.19215 31 male 36.3 2 yes 38711.0 22 male 35.6 0 yes 35585.576 18 female 26.315 0 no 2198.18985 19 female 28.6 5 no 4687.797 63 male 28.31 0 no 13770.0979 28 male 36.4 1 yes 51194.55914 19 male 20.425 0 no 1625.43375 62 female 32.965 3 no 15612.19335 26 male 20.8 0 no 2302.3 35 male 36.67 1 yes 39774.2763 60 male 39.9 0 yes 48173.361 24 female 26.6 0 no 3046.062 31 female 36.63 2 no 4949.7587 41 male 21.78 1 no 6272.4772 37 female 30.8 2 no 6313.759 38 male 37.05 1 no 6079.6715 55 male 37.3 0 no 20630.28351 18 female 38.665 2 no 3393.35635 28 female 34.77 0 no 3556.9223 60 female 24.53 0 no 12629.8967 36 male 35.2 1 yes 38709.176 18 female 35.625 0 no 2211.13075 21 female 33.63 2 no 3579.8287 48 male 28.0 1 yes 23568.272 36 male 34.43 0 yes 37742.5757 40 female 28.69 3 no 8059.6791 58 male 36.955 2 yes 47496.49445 58 female 31.825 2 no 13607.36875 18 male 31.68 2 yes 34303.1672 53 female 22.88 1 yes 23244.7902 34 female 37.335 2 no 5989.52365 43 male 27.36 3 no 8606.2174 25 male 33.66 4 no 4504.6624 64 male 24.7 1 no 30166.61817 28 female 25.935 1 no 4133.64165 20 female 22.42 0 yes 14711.7438 19 female 28.9 0 no 1743.214 61 female 39.1 2 no 14235.072 40 male 26.315 1 no 6389.37785 40 female 36.19 0 no 5920.1041 28 male 23.98 3 yes 17663.1442 27 female 24.75 0 yes 16577.7795 31 male 28.5 5 no 6799.458 53 female 28.1 3 no 11741.726 58 male 32.01 1 no 11946.6259 44 male 27.4 2 no 7726.854 57 male 34.01 0 no 11356.6609 29 female 29.59 1 no 3947.4131 21 male 35.53 0 no 1532.4697 22 female 39.805 0 no 2755.02095 41 female 32.965 0 no 6571.02435 31 male 26.885 1 no 4441.21315 45 female 38.285 0 no 7935.29115 22 male 37.62 1 yes 37165.1638 48 female 41.23 4 no 11033.6617 37 female 34.8 2 yes 39836.519 45 male 22.895 2 yes 21098.55405 57 female 31.16 0 yes 43578.9394 56 female 27.2 0 no 11073.176 46 female 27.74 0 no 8026.6666 55 female 26.98 0 no 11082.5772 21 female 39.49 0 no 2026.9741 53 female 24.795 1 no 10942.13205 59 male 29.83 3 yes 30184.9367 35 male 34.77 2 no 5729.0053 64 female 31.3 2 yes 47291.055 28 female 37.62 1 no 3766.8838 54 female 30.8 3 no 12105.32 55 male 38.28 0 no 10226.2842 56 male 19.95 0 yes 22412.6485 38 male 19.3 0 yes 15820.699 41 female 31.6 0 no 6186.127 30 male 25.46 0 no 3645.0894 18 female 30.115 0 no 21344.8467 61 female 29.92 3 yes 30942.1918 34 female 27.5 1 no 5003.853 20 male 28.025 1 yes 17560.37975 19 female 28.4 1 no 2331.519 26 male 30.875 2 no 3877.30425 29 male 27.94 0 no 2867.1196 63 male 35.09 0 yes 47055.5321 54 male 33.63 1 no 10825.2537 55 female 29.7 2 no 11881.358 37 male 30.8 0 no 4646.759 21 female 35.72 0 no 2404.7338 52 male 32.205 3 no 11488.31695 60 male 28.595 0 no 30259.99556 58 male 49.06 0 no 11381.3254 29 female 27.94 1 yes 19107.7796 49 female 27.17 0 no 8601.3293 37 female 23.37 2 no 6686.4313 44 male 37.1 2 no 7740.337 18 male 23.75 0 no 1705.6245 20 female 28.975 0 no 2257.47525 44 male 31.35 1 yes 39556.4945 47 female 33.915 3 no 10115.00885 26 female 28.785 0 no 3385.39915 19 female 28.3 0 yes 17081.08 52 female 37.4 0 no 9634.538 32 female 17.765 2 yes 32734.1863 38

In [0]:
from pyspark.sql.functions import regexp_replace
insurance1=insurance.withColumn('smoker', regexp_replace('smoker', 'yes', '1'))
insurance2=insurance1.withColumn('smoker', regexp_replace('smoker', 'no', '0'))


#### b) Perform a multiple linear regression in an attempt to predict the health insurance charges based on the clients information. At the end report the coeficients, the RMSE and the r2 of the model: (2.5)

##### Make sure to consider any transformation necessary to the dataframe (e.g., deriving new variables, dropping existing ones, scale transformations , etc...) Justify all your decisions.

In [0]:
insurance3=insurance2.withColumn('sex', regexp_replace('sex', 'female', '1'))
insurance4=insurance3.withColumn('sex', regexp_replace('sex', 'male', '0'))
display(insurance4)
type(insurance4)

age sex bmi children smoker charges 19 1 27.9 0 1 16884.924 18 0 33.77 1 0 1725.5523 28 0 33.0 3 0 4449.462 33 0 22.705 0 0 21984.47061 32 0 28.88 0 0 3866.8552 31 1 25.74 0 0 3756.6216 46 1 33.44 1 0 8240.5896 37 1 27.74 3 0 7281.5056 37 0 29.83 2 0 6406.4107 60 1 25.84 0 0 28923.13692 25 0 26.22 0 0 2721.3208 62 1 26.29 0 1 27808.7251 23 0 34.4 0 0 1826.843 56 1 39.82 0 0 11090.7178 27 0 42.13 0 1 39611.7577 19 0 24.6 1 0 1837.237 52 1 30.78 1 0 10797.3362 23 0 23.845 0 0 2395.17155 56 0 40.3 0 0 10602.385 30 0 35.3 0 1 36837.467 60 1 36.005 0 0 13228.84695 30 1 32.4 1 0 4149.736 18 0 34.1 0 0 1137.011 34 1 31.92 1 1 37701.8768 37 0 28.025 2 0 6203.90175 59 1 27.72 3 0 14001.1338 63 1 23.085 0 0 14451.83515 55 1 32.775 2 0 12268.63225 23 0 17.385 1 0 2775.19215 31 0 36.3 2 1 38711.0 22 0 35.6 0 1 35585.576 18 1 26.315 0 0 2198.18985 19 1 28.6 5 0 4687.797 63 0 28.31 0 0 13770.0979 28 0 36.4 1 1 51194.55914 19 0 20.425 0 0 1625.43375 62 1 32.965 3 0 15612.19335 26 0 20.8 0 0 2302.3 35 0 36.67 1 1 39774.2763 60 0 39.9 0 1 48173.361 24 1 26.6 0 0 3046.062 31 1 36.63 2 0 4949.7587 41 0 21.78 1 0 6272.4772 37 1 30.8 2 0 6313.759 38 0 37.05 1 0 6079.6715 55 0 37.3 0 0 20630.28351 18 1 38.665 2 0 3393.35635 28 1 34.77 0 0 3556.9223 60 1 24.53 0 0 12629.8967 36 0 35.2 1 1 38709.176 18 1 35.625 0 0 2211.13075 21 1 33.63 2 0 3579.8287 48 0 28.0 1 1 23568.272 36 0 34.43 0 1 37742.5757 40 1 28.69 3 0 8059.6791 58 0 36.955 2 1 47496.49445 58 1 31.825 2 0 13607.36875 18 0 31.68 2 1 34303.1672 53 1 22.88 1 1 23244.7902 34 1 37.335 2 0 5989.52365 43 0 27.36 3 0 8606.2174 25 0 33.66 4 0 4504.6624 64 0 24.7 1 0 30166.61817 28 1 25.935 1 0 4133.64165 20 1 22.42 0 1 14711.7438 19 1 28.9 0 0 1743.214 61 1 39.1 2 0 14235.072 40 0 26.315 1 0 6389.37785 40 1 36.19 0 0 5920.1041 28 0 23.98 3 1 17663.1442 27 1 24.75 0 1 16577.7795 31 0 28.5 5 0 6799.458 53 1 28.1 3 0 11741.726 58 0 32.01 1 0 11946.6259 44 0 27.4 2 0 7726.854 57 0 34.01 0 0 11356.6609 29 1 29.59 1 0 3947.4131 21 0 35.53 0 0 1532.4697 22 1 39.805 0 0 2755.02095 41 1 32.965 0 0 6571.02435 31 0 26.885 1 0 4441.21315 45 1 38.285 0 0 7935.29115 22 0 37.62 1 1 37165.1638 48 1 41.23 4 0 11033.6617 37 1 34.8 2 1 39836.519 45 0 22.895 2 1 21098.55405 57 1 31.16 0 1 43578.9394 56 1 27.2 0 0 11073.176 46 1 27.74 0 0 8026.6666 55 1 26.98 0 0 11082.5772 21 1 39.49 0 0 2026.9741 53 1 24.795 1 0 10942.13205 59 0 29.83 3 1 30184.9367 35 0 34.77 2 0 5729.0053 64 1 31.3 2 1 47291.055 28 1 37.62 1 0 3766.8838 54 1 30.8 3 0 12105.32 55 0 38.28 0 0 10226.2842 56 0 19.95 0 1 22412.6485 38 0 19.3 0 1 15820.699 41 1 31.6 0 0 6186.127 30 0 25.46 0 0 3645.0894 18 1 30.115 0 0 21344.8467 61 1 29.92 3 1 30942.1918 34 1 27.5 1 0 5003.853 20 0 28.025 1 1 17560.37975 19 1 28.4 1 0 2331.519 26 0 30.875 2 0 3877.30425 29 0 27.94 0 0 2867.1196 63 0 35.09 0 1 47055.5321 54 0 33.63 1 0 10825.2537 55 1 29.7 2 0 11881.358 37 0 30.8 0 0 4646.759 21 1 35.72 0 0 2404.7338 52 0 32.205 3 0 11488.31695 60 0 28.595 0 0 30259.99556 58 0 49.06 0 0 11381.3254 29 1 27.94 1 1 19107.7796 49 1 27.17 0 0 8601.3293 37 1 23.37 2 0 6686.4313 44 0 37.1 2 0 7740.337 18 0 23.75 0 0 1705.6245 20 1 28.975 0 0 2257.47525 44 0 31.35 1 1 39556.4945 47 1 33.915 3 0 10115.00885 26 1 28.785 0 0 3385.39915 19 1 28.3 0 1 17081.08 52 1 37.4 0 0 9634.538 32 1 17.765 2 1 32734.1863 38 0 34.7 2 0 6082.405 59 1 26.505 0 0 12815.44495 61 1 22.04 0 0 13616.3586 53 1 35.9 2 0 11163.568 19 0 25.555 0 0 1632.56445 20 1 28.785 0 0 2457.21115 22 1 28.05 0 0 2155.6815 19 0 34.1 0 0 1261.442 22 0 25.175 0 0 2045.68525 54 1 31.9 3 0 27322.73386 22 1 36.0 0 0 2166.732 34 0 22.42 2 0 27375.90478 26 0 32.49 1 0 3490.5491 34 0 25.3 2 1 18972.495 29 0 29.735 2 0 18157.876 30 0 28.69 3 1 20745.9891 29 1 38.83 3 0 5138.2567 46 0 30.495 3 1 40720.55105 51 1 37.73 1 0 9877.6077 53 1 37.43 1 0 10959.6947 19 0 28.4 1 0 1842.519 35 0 24.13 1 0 5125.2157 48 0 29.7 0 0 7789.635 32 1 37.145 3 0 6334.34355 42 1 23.37 0 1 19964.7463 40 1 25.46 1 0 7077.1894 44 0 39.52 0 0 6948.7008 4

Out[328]: pyspark.sql.dataframe.DataFrame

In [0]:
insurance4.dtypes

Out[329]: [('age', 'int'),
 ('sex', 'string'),
 ('bmi', 'double'),
 ('children', 'int'),
 ('smoker', 'string'),
 ('charges', 'double')]

In [0]:
insurance4.createOrReplaceTempView("insurance4")
insurance5=(spark.sql("select age, CAST(sex as INT) as sex, bmi, children, CAST(smoker as INT) as smoker, charges from insurance4"))
display(insurance5)

age sex bmi children smoker charges 19 1 27.9 0 1 16884.924 18 0 33.77 1 0 1725.5523 28 0 33.0 3 0 4449.462 33 0 22.705 0 0 21984.47061 32 0 28.88 0 0 3866.8552 31 1 25.74 0 0 3756.6216 46 1 33.44 1 0 8240.5896 37 1 27.74 3 0 7281.5056 37 0 29.83 2 0 6406.4107 60 1 25.84 0 0 28923.13692 25 0 26.22 0 0 2721.3208 62 1 26.29 0 1 27808.7251 23 0 34.4 0 0 1826.843 56 1 39.82 0 0 11090.7178 27 0 42.13 0 1 39611.7577 19 0 24.6 1 0 1837.237 52 1 30.78 1 0 10797.3362 23 0 23.845 0 0 2395.17155 56 0 40.3 0 0 10602.385 30 0 35.3 0 1 36837.467 60 1 36.005 0 0 13228.84695 30 1 32.4 1 0 4149.736 18 0 34.1 0 0 1137.011 34 1 31.92 1 1 37701.8768 37 0 28.025 2 0 6203.90175 59 1 27.72 3 0 14001.1338 63 1 23.085 0 0 14451.83515 55 1 32.775 2 0 12268.63225 23 0 17.385 1 0 2775.19215 31 0 36.3 2 1 38711.0 22 0 35.6 0 1 35585.576 18 1 26.315 0 0 2198.18985 19 1 28.6 5 0 4687.797 63 0 28.31 0 0 13770.0979 28 0 36.4 1 1 51194.55914 19 0 20.425 0 0 1625.43375 62 1 32.965 3 0 15612.19335 26 0 20.8 0 0 2302.3 35 0 36.67 1 1 39774.2763 60 0 39.9 0 1 48173.361 24 1 26.6 0 0 3046.062 31 1 36.63 2 0 4949.7587 41 0 21.78 1 0 6272.4772 37 1 30.8 2 0 6313.759 38 0 37.05 1 0 6079.6715 55 0 37.3 0 0 20630.28351 18 1 38.665 2 0 3393.35635 28 1 34.77 0 0 3556.9223 60 1 24.53 0 0 12629.8967 36 0 35.2 1 1 38709.176 18 1 35.625 0 0 2211.13075 21 1 33.63 2 0 3579.8287 48 0 28.0 1 1 23568.272 36 0 34.43 0 1 37742.5757 40 1 28.69 3 0 8059.6791 58 0 36.955 2 1 47496.49445 58 1 31.825 2 0 13607.36875 18 0 31.68 2 1 34303.1672 53 1 22.88 1 1 23244.7902 34 1 37.335 2 0 5989.52365 43 0 27.36 3 0 8606.2174 25 0 33.66 4 0 4504.6624 64 0 24.7 1 0 30166.61817 28 1 25.935 1 0 4133.64165 20 1 22.42 0 1 14711.7438 19 1 28.9 0 0 1743.214 61 1 39.1 2 0 14235.072 40 0 26.315 1 0 6389.37785 40 1 36.19 0 0 5920.1041 28 0 23.98 3 1 17663.1442 27 1 24.75 0 1 16577.7795 31 0 28.5 5 0 6799.458 53 1 28.1 3 0 11741.726 58 0 32.01 1 0 11946.6259 44 0 27.4 2 0 7726.854 57 0 34.01 0 0 11356.6609 29 1 29.59 1 0 3947.4131 21 0 35.53 0 0 1532.4697 22 1 39.805 0 0 2755.02095 41 1 32.965 0 0 6571.02435 31 0 26.885 1 0 4441.21315 45 1 38.285 0 0 7935.29115 22 0 37.62 1 1 37165.1638 48 1 41.23 4 0 11033.6617 37 1 34.8 2 1 39836.519 45 0 22.895 2 1 21098.55405 57 1 31.16 0 1 43578.9394 56 1 27.2 0 0 11073.176 46 1 27.74 0 0 8026.6666 55 1 26.98 0 0 11082.5772 21 1 39.49 0 0 2026.9741 53 1 24.795 1 0 10942.13205 59 0 29.83 3 1 30184.9367 35 0 34.77 2 0 5729.0053 64 1 31.3 2 1 47291.055 28 1 37.62 1 0 3766.8838 54 1 30.8 3 0 12105.32 55 0 38.28 0 0 10226.2842 56 0 19.95 0 1 22412.6485 38 0 19.3 0 1 15820.699 41 1 31.6 0 0 6186.127 30 0 25.46 0 0 3645.0894 18 1 30.115 0 0 21344.8467 61 1 29.92 3 1 30942.1918 34 1 27.5 1 0 5003.853 20 0 28.025 1 1 17560.37975 19 1 28.4 1 0 2331.519 26 0 30.875 2 0 3877.30425 29 0 27.94 0 0 2867.1196 63 0 35.09 0 1 47055.5321 54 0 33.63 1 0 10825.2537 55 1 29.7 2 0 11881.358 37 0 30.8 0 0 4646.759 21 1 35.72 0 0 2404.7338 52 0 32.205 3 0 11488.31695 60 0 28.595 0 0 30259.99556 58 0 49.06 0 0 11381.3254 29 1 27.94 1 1 19107.7796 49 1 27.17 0 0 8601.3293 37 1 23.37 2 0 6686.4313 44 0 37.1 2 0 7740.337 18 0 23.75 0 0 1705.6245 20 1 28.975 0 0 2257.47525 44 0 31.35 1 1 39556.4945 47 1 33.915 3 0 10115.00885 26 1 28.785 0 0 3385.39915 19 1 28.3 0 1 17081.08 52 1 37.4 0 0 9634.538 32 1 17.765 2 1 32734.1863 38 0 34.7 2 0 6082.405 59 1 26.505 0 0 12815.44495 61 1 22.04 0 0 13616.3586 53 1 35.9 2 0 11163.568 19 0 25.555 0 0 1632.56445 20 1 28.785 0 0 2457.21115 22 1 28.05 0 0 2155.6815 19 0 34.1 0 0 1261.442 22 0 25.175 0 0 2045.68525 54 1 31.9 3 0 27322.73386 22 1 36.0 0 0 2166.732 34 0 22.42 2 0 27375.90478 26 0 32.49 1 0 3490.5491 34 0 25.3 2 1 18972.495 29 0 29.735 2 0 18157.876 30 0 28.69 3 1 20745.9891 29 1 38.83 3 0 5138.2567 46 0 30.495 3 1 40720.55105 51 1 37.73 1 0 9877.6077 53 1 37.43 1 0 10959.6947 19 0 28.4 1 0 1842.519 35 0 24.13 1 0 5125.2157 48 0 29.7 0 0 7789.635 32 1 37.145 3 0 6334.34355 42 1 23.37 0 1 19964.7463 40 1 25.46 1 0 7077.1894 44 0 39.52 0 0 6948.7008 4

In [0]:
insurance5.dtypes

Out[331]: [('age', 'int'),
 ('sex', 'int'),
 ('bmi', 'double'),
 ('children', 'int'),
 ('smoker', 'int'),
 ('charges', 'double')]

In [0]:
type(insurance5)

Out[332]: pyspark.sql.dataframe.DataFrame

In [0]:
from pyspark.ml.regression import LinearRegression
#from pyspark.ml.regression import LinearRegressionSummary
from pyspark.ml.feature import VectorAssembler
#from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
from pyspark.ml.feature import MinMaxScaler

In [0]:
# Split the data into training and test sets (20% held out for testing)
(insurance5TrainSet, insurance5TestSet) = insurance5.randomSplit([0.8,0.2])

# Vectorize features
LRAssembler = VectorAssembler(inputCols=insurance5.drop("charges").columns, outputCol="features")

# Configure model
LR = LinearRegression(labelCol="charges")

# Chain Vectorization and Linear Regression in a Pipeline
pipeline = Pipeline(stages=[LRAssembler,LR])

# Train Model
lrModel = pipeline.fit(insurance5TrainSet)

# Make Predictions
lrPredictions = lrModel.transform(insurance5TestSet)
display(lrPredictions)

age sex bmi children smoker charges features prediction 18 0 21.565 0 1 13747.87235 Map(vectorType -> dense, length -> 5, values -> List(18.0, 0.0, 21.565, 0.0, 1.0)) 23240.816552556298 18 0 21.78 2 0 11884.04858 Map(vectorType -> dense, length -> 5, values -> List(18.0, 0.0, 21.78, 2.0, 0.0)) 56.724011198441076 18 0 23.75 0 0 1705.6245 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(18.0, 23.75)) -321.7030604967422 18 0 30.14 0 0 1131.5066 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(18.0, 30.14)) 1865.7442018477414 18 0 33.66 0 0 1136.3994 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(18.0, 33.66)) 3070.7229754709915 18 1 20.79 0 0 1607.5101 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 20.79, 0.0, 0.0)) -900.5875967931133 18 1 26.315 0 0 2198.18985 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 26.315, 0.0, 0.0)) 990.7498248740649 18 1 26.73 0 0 1615.7667 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 26.73, 0.0, 0.0)) 1132.8140836961247 18 1 29.165 0 0 7323.734819 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 29.165, 0.0, 0.0)) 1966.371843290617 18 1 30.305 0 0 2203.73595 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 30.305, 0.0, 0.0)) 2356.62065065724 18 1 31.13 0 0 1621.8827 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 31.13, 0.0, 0.0)) 2639.0375507251883 18 1 33.88 0 0 11482.63485 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 33.88, 0.0, 0.0)) 3580.427217618355 18 1 36.85 0 0 1629.8335 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 36.85, 0.0, 0.0)) 4597.128057862974 18 1 38.665 2 0 3393.35635 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 38.665, 2.0, 0.0)) 6271.249634718384 19 0 19.8 0 0 1241.565 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(19.0, 19.8)) -1416.7326994283758 19 0 25.555 1 0 2221.56445 Map(vectorType -> dense, length -> 5, values -> List(19.0, 0.0, 25.555, 1.0, 0.0)) 1079.7413290955556 19 0 30.4 0 0 1256.299 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(19.0, 30.4)) 2211.8965620507333 19 0 30.59 0 0 1639.5631 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(19.0, 30.59)) 2276.9380299451695 19 0 34.8 0 1 34779.615 Map(vectorType -> dense, length -> 5, values -> List(19.0, 0.0, 34.8, 0.0, 1.0)) 28028.616522918866 19 1 17.8 0 0 1727.785 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 17.8, 0.0, 0.0)) -1666.9866611002217 19 1 18.6 0 0 1728.897 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 18.6, 0.0, 0.0)) -1393.12784891312 19 1 24.7 0 0 1737.376 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 24.7, 0.0, 0.0)) 695.0455940135362 19 1 28.3 0 1 17081.08 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 28.3, 0.0, 1.0)) 26237.906742694566 19 1 28.6 5 0 4687.797 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 28.6, 5.0, 0.0)) 4662.118295190474 19 1 28.88 0 1 17748.5062 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 28.88, 0.0, 1.0)) 26436.454381530213 19 1 34.7 2 1 36397.576 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 34.7, 2.0, 1.0)) 29481.581636897306 19 1 36.575 0 0 2136.88225 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 36.575, 0.0, 0.0)) 4760.137337415843 20 0 22.0 1 0 1964.78 Map(vectorType -> dense, length -> 5, values -> List(20.0, 0.0, 22.0, 1.0, 0.0)) 119.9294786813025 20 0 29.735 0 0 1769.53165 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(20.0, 29.735)) 2241.399670662391 20 1 33.3 0 0 1880.487 Map(vectorType -> dense, length -> 5, values -> List(20.0, 1.0, 33.3, 0.0, 0.0)) 3896.1760712670766 20 1 37.0 5 0 4830.63 Map(vectorType -> dense, length -> 5, values -> List(20.0, 1.0, 37.0, 5.0, 0.0)) 7794.78406

In [0]:

# Show Predictions
display(lrPredictions.select("charges","prediction","features"))

charges prediction features 13747.87235 23240.816552556298 Map(vectorType -> dense, length -> 5, values -> List(18.0, 0.0, 21.565, 0.0, 1.0)) 11884.04858 56.724011198441076 Map(vectorType -> dense, length -> 5, values -> List(18.0, 0.0, 21.78, 2.0, 0.0)) 1705.6245 -321.7030604967422 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(18.0, 23.75)) 1131.5066 1865.7442018477414 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(18.0, 30.14)) 1136.3994 3070.7229754709915 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(18.0, 33.66)) 1607.5101 -900.5875967931133 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 20.79, 0.0, 0.0)) 2198.18985 990.7498248740649 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 26.315, 0.0, 0.0)) 1615.7667 1132.8140836961247 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 26.73, 0.0, 0.0)) 7323.734819 1966.371843290617 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 29.165, 0.0, 0.0)) 2203.73595 2356.62065065724 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 30.305, 0.0, 0.0)) 1621.8827 2639.0375507251883 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 31.13, 0.0, 0.0)) 11482.63485 3580.427217618355 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 33.88, 0.0, 0.0)) 1629.8335 4597.128057862974 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 36.85, 0.0, 0.0)) 3393.35635 6271.249634718384 Map(vectorType -> dense, length -> 5, values -> List(18.0, 1.0, 38.665, 2.0, 0.0)) 1241.565 -1416.7326994283758 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(19.0, 19.8)) 2221.56445 1079.7413290955556 Map(vectorType -> dense, length -> 5, values -> List(19.0, 0.0, 25.555, 1.0, 0.0)) 1256.299 2211.8965620507333 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(19.0, 30.4)) 1639.5631 2276.9380299451695 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(19.0, 30.59)) 34779.615 28028.616522918866 Map(vectorType -> dense, length -> 5, values -> List(19.0, 0.0, 34.8, 0.0, 1.0)) 1727.785 -1666.9866611002217 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 17.8, 0.0, 0.0)) 1728.897 -1393.12784891312 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 18.6, 0.0, 0.0)) 1737.376 695.0455940135362 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 24.7, 0.0, 0.0)) 17081.08 26237.906742694566 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 28.3, 0.0, 1.0)) 4687.797 4662.118295190474 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 28.6, 5.0, 0.0)) 17748.5062 26436.454381530213 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 28.88, 0.0, 1.0)) 36397.576 29481.581636897306 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 34.7, 2.0, 1.0)) 2136.88225 4760.137337415843 Map(vectorType -> dense, length -> 5, values -> List(19.0, 1.0, 36.575, 0.0, 0.0)) 1964.78 119.9294786813025 Map(vectorType -> dense, length -> 5, values -> List(20.0, 0.0, 22.0, 1.0, 0.0)) 1769.53165 2241.399670662391 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(20.0, 29.735)) 1880.487 3896.1760712670766 Map(vectorType -> dense, length -> 5, values -> List(20.0, 1.0, 33.3, 0.0, 0.0)) 4830.63 7794.784069397239 Map(vectorType -> dense, length -> 5, values -> List(20.0, 1.0, 37.0, 5.0, 0.0)) 3861.20965 825.6811172416183 Map(vectorType -> dense, length -> 5, values -> List(21.0, 0.0, 20.235, 3.0, 0.0)) 1515.3449 264.8869800035209 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(21.0, 23.21)) 16586.49771 2938.4336339801084 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(21.0, 31.02)) 1909.52745 3018.879660060069 Map(vectorType -> sparse, length -> 5, indices -> List(0, 2), values -> List(21.0, 31.255)) 3167.45

In [0]:
print("Coefficients:")
coefficients = lrModel.stages[1].coefficients
i=0
for feature in insurance5.drop("charges").columns:
  print(feature,":",coefficients[i])
  i+=1
print()
print("Coefficients List: %s" % str(lrModel.stages[1].coefficients))
print("Intercept: %s" % str(lrModel.stages[1].intercept))

Coefficients:
age : 257.1482462421855
sex : 434.3930687959098
bmi : 342.32351523387825
children : 526.4021983529622
smoker : 24310.496493839066

Coefficients List: [257.1482462421855,434.3930687959098,342.32351523387825,526.4021983529622,24310.496493839066]
Intercept: -13080.55497966069


In [0]:
trainingSummary = lrModel.stages[1].summary
print("RMSE: %f" % trainingSummary.rootMeanSquaredError)
print("R2  : %f" % trainingSummary.r2)
trainingSummary.residuals.show()

RMSE: 6063.794231
R2  : 0.759682
+-------------------+
|          residuals|
+-------------------+
|  4683.199644168654|
|-10000.732821637397|
|  2804.655975229986|
| 2286.4370320744906|
| 2254.0483481272704|
| 1628.4316587230364|
| 1653.5267736943483|
| -8958.424192550601|
|  1444.331249446811|
| 1217.6104618162806|
|  741.0547217724934|
| -8572.301121689583|
|  9506.637022677294|
| 407.89336313582066|
|  -409.120993470616|
| -634.1371135249735|
| -52.08691086743647|
|  6546.943894147105|
|  7012.151615091327|
| -1821.815515443809|
+-------------------+
only showing top 20 rows



# PART C:

## <span style="color:blue"> **Show us what you got! (2 points):** </span>

<img src ='https://media.tenor.com/images/d8f45316e96078d93b36374474b67bf6/tenor.png'>

##### a) Using the cleaned e-commerce dataset from Part A, search for interesting variables that could be related to the countries' purchases. You should obtain the data regarding the countries' characteristics from the Macroeconomics sector of Pordata https://www.pordata.pt/en/Theme/Europe/Macroeconomics-32

###### You should limit your analysis to no more than six countries of your choice from the e-commerce dataset.

- The idea is that you find a way to associate some variables from Pordata and the purchases dataset. Ask yourselves the following questions: **What can explain/contribute to the fact that some countries buy more? or less? What can be related to the number of sales? Or the total value of sales?**... The questions are endless! Try to be creative and look for some associations!

###### You will be evaluated based on the logic used to solve this problem, the "investigation questions" you raise, the adequacy of your methodologies and your creativity.

##### MAKE SURE YOU COMMENT YOUR LOGIC AND "TELL YOUR STORY". WHAT QUESTIONS DID YOU RAISE? HOW DID YOU SEEK TO ANSWER THEM?

In [0]:
Pordata_consumption = spark.read.csv("dbfs:/FileStore/Pordata_consumption-1.csv", header="true", sep=",", inferSchema="true")
display(Pordata_consumption)

Countries Total Durable_goods Semi_durable_goods Non_durable_goods Services DE - Germany 1397122 160441 129965 395962 710754 AT - Austria 165634 18452 16536 45294 85351 BE - Belgium 186615 15551 15218 58456 97391 BG - Bulgaria 27857 2368 1945 10876 12669 CY - Cyprus 13786 898 965 4352 7571 HR - Croatia 31961 1868 2118 13497 14478 DK - Denmark 114907 10576 11118 31344 61869 SK - Slovakia 39257 3180 2727 15773 17577 SI - Slovenia 21760 1936 1914 8856 9054 ES - Spain 640903 39960 47348 183974 369621 EE - Estonia 8566 556 818 3799 3392 FI - Finland 100466 9488 8981 30723 51274 FR - France 1106046 98559 89320 337781 580389 GR - Greece 147404 6701 10603 49047 81053 HU - Hungary 55116 3198 3628 24020 24270 IE - Ireland 75127 4073 5288 26892 38875 IT - Italy 1013276 78912 98668 324405 511291 LV - Latvia 11825 513 946 5473 4894 LT - Lithuania 19657 1372 2150 10958 5177 LU - Luxembourg 16143 1378 1466 5670 7629 MT - Malta 4845 434 425 1599 2387 NL - Netherlands 288380 28014 26869 79598 153899 PL - Poland 231157 14669 18548 106594 91346 PT - Portugal 117956 9430 8889 40089 59548 CZ - Czech Republic 83941 6769 5349 33667 38157 RO - Romania 81607 6433 5209 41862 28103 SE - Sweden 185620 17621 17586 54623 95790 IS - Iceland 5450 281 551 1807 2811 NO - Norway 132516 17250 12993 38538 63736 UK - United Kingdom 1166220 104296 119230 271398 671297

In [0]:
Pordata_consumption.createOrReplaceTempView("Pordata_consumption")
Pordata_consumption_1=(spark.sql("select SUBSTRING(Countries, charindex('- ',Countries)+2) as Country, Durable_goods+Semi_durable_goods+Non_durable_goods as Total_Goods, * from Pordata_consumption"))
Pordata_consumption_1.createOrReplaceTempView("Pordata_consumption_1")
display(Pordata_consumption_1)

Country Total_Goods Countries Total Durable_goods Semi_durable_goods Non_durable_goods Services Germany 686368 DE - Germany 1397122 160441 129965 395962 710754 Austria 80282 AT - Austria 165634 18452 16536 45294 85351 Belgium 89225 BE - Belgium 186615 15551 15218 58456 97391 Bulgaria 15189 BG - Bulgaria 27857 2368 1945 10876 12669 Cyprus 6215 CY - Cyprus 13786 898 965 4352 7571 Croatia 17483 HR - Croatia 31961 1868 2118 13497 14478 Denmark 53038 DK - Denmark 114907 10576 11118 31344 61869 Slovakia 21680 SK - Slovakia 39257 3180 2727 15773 17577 Slovenia 12706 SI - Slovenia 21760 1936 1914 8856 9054 Spain 271282 ES - Spain 640903 39960 47348 183974 369621 Estonia 5173 EE - Estonia 8566 556 818 3799 3392 Finland 49192 FI - Finland 100466 9488 8981 30723 51274 France 525660 FR - France 1106046 98559 89320 337781 580389 Greece 66351 GR - Greece 147404 6701 10603 49047 81053 Hungary 30846 HU - Hungary 55116 3198 3628 24020 24270 Ireland 36253 IE - Ireland 75127 4073 5288 26892 38875 Italy 501985 IT - Italy 1013276 78912 98668 324405 511291 Latvia 6932 LV - Latvia 11825 513 946 5473 4894 Lithuania 14480 LT - Lithuania 19657 1372 2150 10958 5177 Luxembourg 8514 LU - Luxembourg 16143 1378 1466 5670 7629 Malta 2458 MT - Malta 4845 434 425 1599 2387 Netherlands 134481 NL - Netherlands 288380 28014 26869 79598 153899 Poland 139811 PL - Poland 231157 14669 18548 106594 91346 Portugal 58408 PT - Portugal 117956 9430 8889 40089 59548 Czech Republic 45785 CZ - Czech Republic 83941 6769 5349 33667 38157 Romania 53504 RO - Romania 81607 6433 5209 41862 28103 Sweden 89830 SE - Sweden 185620 17621 17586 54623 95790 Iceland 2639 IS - Iceland 5450 281 551 1807 2811 Norway 68781 NO - Norway 132516 17250 12993 38538 63736 United Kingdom 494924 UK - United Kingdom 1166220 104296 119230 271398 671297

In [0]:
Pordata_savingrate = spark.read.csv("dbfs:/FileStore/Pordata_savingrate-2.csv", header="true", sep=",", inferSchema="true")
display(Pordata_savingrate)

Countries Savings_rat_of_households DE - Germany 0.0 AT - Austria 0.0 BE - Belgium 15.4 BG - Bulgaria 0.0 CY - Cyprus 5.0 HR - Croatia 9.2 DK - Denmark 8.3 SK - Slovakia 8.4 SI - Slovenia 11.4 ES - Spain 10.0 EE - Estonia 9.6 FI - Finland 8.5 FR - France 15.6 GR - Greece 1.0 HU - Hungary 11.9 IE - Ireland 10.2 IT - Italy 10.9 LV - Latvia 0.4 LT - Lithuania 4.4 LU - Luxembourg 13.1 MT - Malta 0.0 NL - Netherlands 14.7 PL - Poland 3.2 PT - Portugal 8.8 CZ - Czech Republic 11.6 RO - Romania 0.0 SE - Sweden 14.3 UK - United Kingdom 9.9

In [0]:
Pordata_savingrate.createOrReplaceTempView("Pordata_savingrate")
Pordata_savingrate_1=(spark.sql("select SUBSTRING(Countries, charindex('- ',Countries)+2) as Country, Savings_rat_of_households as Savings_rate_of_households from Pordata_savingrate"))
Pordata_savingrate_1.createOrReplaceTempView("Pordata_savingrate_1")
display(Pordata_savingrate_1)

Country Savings_rate_of_households Germany 0.0 Austria 0.0 Belgium 15.4 Bulgaria 0.0 Cyprus 5.0 Croatia 9.2 Denmark 8.3 Slovakia 8.4 Slovenia 11.4 Spain 10.0 Estonia 9.6 Finland 8.5 France 15.6 Greece 1.0 Hungary 11.9 Ireland 10.2 Italy 10.9 Latvia 0.4 Lithuania 4.4 Luxembourg 13.1 Malta 0.0 Netherlands 14.7 Poland 3.2 Portugal 8.8 Czech Republic 11.6 Romania 0.0 Sweden 14.3 United Kingdom 9.9

In [0]:
Pordata_GDP = spark.read.csv("dbfs:/FileStore/Pordata_GDP-1.csv", header="true", sep=",", inferSchema="true")
display(Pordata_GDP)


Countries GDP DE - Germany 2693560.0 AT - Austria 310128.7 BE - Belgium 375967.8 BG - Bulgaria 41478.9 CY - Cyprus 19803.0 HR - Croatia 45378.6 DK - Denmark 247879.9 SK - Slovakia 71477.1 SI - Slovenia 37058.6 ES - Spain 1063763.0 EE - Estonia 16677.3 FI - Finland 197998.0 FR - France 2058369.0 GR - Greece 203308.2 HU - Hungary 102193.5 IE - Ireland 171683.4 IT - Italy 1648755.8 LV - Latvia 19666.0 LT - Lithuania 31317.2 LU - Luxembourg 44323.5 MT - Malta 6924.6 NL - Netherlands 650359.0 PL - Poland 379860.0 PT - Portugal 176096.2 CZ - Czech Republic 165202.2 RO - Romania 131841.6 SE - Sweden 412844.7 IS - Iceland 10934.3 NO - Norway 358339.5 UK - United Kingdom 1912869.3 CH - Switzerland 520201.4

In [0]:
Pordata_GDP.createOrReplaceTempView("Pordata_GDP")
Pordata_GDP_1=(spark.sql("select SUBSTRING(Countries, charindex('- ',Countries)+2) as Country, * from Pordata_GDP"))
Pordata_GDP_1.createOrReplaceTempView("Pordata_GDP_1")
display(Pordata_GDP_1)

Country Countries GDP Germany DE - Germany 2693560.0 Austria AT - Austria 310128.7 Belgium BE - Belgium 375967.8 Bulgaria BG - Bulgaria 41478.9 Cyprus CY - Cyprus 19803.0 Croatia HR - Croatia 45378.6 Denmark DK - Denmark 247879.9 Slovakia SK - Slovakia 71477.1 Slovenia SI - Slovenia 37058.6 Spain ES - Spain 1063763.0 Estonia EE - Estonia 16677.3 Finland FI - Finland 197998.0 France FR - France 2058369.0 Greece GR - Greece 203308.2 Hungary HU - Hungary 102193.5 Ireland IE - Ireland 171683.4 Italy IT - Italy 1648755.8 Latvia LV - Latvia 19666.0 Lithuania LT - Lithuania 31317.2 Luxembourg LU - Luxembourg 44323.5 Malta MT - Malta 6924.6 Netherlands NL - Netherlands 650359.0 Poland PL - Poland 379860.0 Portugal PT - Portugal 176096.2 Czech Republic CZ - Czech Republic 165202.2 Romania RO - Romania 131841.6 Sweden SE - Sweden 412844.7 Iceland IS - Iceland 10934.3 Norway NO - Norway 358339.5 United Kingdom UK - United Kingdom 1912869.3 Switzerland CH - Switzerland 520201.4

In [0]:
CountryDF5=(spark.sql("select distinct country from retailDF5"))
CountryDF5.createOrReplaceTempView("CountryDF5")
display(CountryDF5)

country Sweden Singapore Germany France Greece Belgium Finland Italy EIRE Spain Iceland Channel Islands Cyprus Switzerland Lebanon Poland Portugal Australia United Kingdom Netherlands Norway Denmark Israel Saudi Arabia United Arab Emirates Canada Czech Republic Japan Austria European Community Malta Unspecified USA Brazil Bahrain RSA

In [0]:
retailDF_F=(spark.sql("select country, round(SUM(AmountSpent),2) AS AmountSpent, COUNT(DISTINCT(InvoiceNO)) AS Orders from retailDF5 group by country"))
retailDF_F.createOrReplaceTempView("retailDF_F")
display(retailDF_F)

country AmountSpent Orders Sweden 34544.03 34 Singapore 21279.29 7 Germany 213626.0 427 RSA 1002.31 1 France 199407.74 368 Greece 4760.52 5 European Community 1300.25 4 Belgium 39386.43 93 Finland 21653.28 40 Malta 2725.59 5 Unspecified 2667.07 8 Italy 16671.74 36 EIRE 256732.02 245 Norway 32378.32 34 Spain 59733.38 86 Denmark 17673.84 17 Iceland 3598.21 6 Israel 7221.69 5 Channel Islands 20086.91 25 USA 3580.39 5 Cyprus 11999.56 15 Saudi Arabia 145.92 1 Switzerland 55139.03 49 United Arab Emirates 1902.28 3 Canada 3666.38 6 Czech Republic 826.74 2 Brazil 1143.6 1 Lebanon 1693.88 1 Japan 29711.3 16 Poland 7086.49 18 Portugal 30999.92 51 Australia 137488.46 54 Austria 9921.48 16 Bahrain 548.4 2 United Kingdom 6809729.7 15358 Netherlands 276661.86 92

In [0]:
retail_pordata=(spark.sql("select f.country, f.AmountSpent, f.Orders, g.GDP, c.Total_Goods, s.Savings_rate_of_households from retailDF_F as f LEFT JOIN Pordata_GDP_1 as g ON f.country=g.Country  LEFT JOIN Pordata_consumption_1 as C ON f.country=C.Country LEFT JOIN Pordata_savingrate_1 as s ON f.country=s.Country order by 1"))
retail_pordata.createOrReplaceTempView("retail_pordata")
display(retail_pordata)

country AmountSpent Orders GDP Total_Goods Savings_rate_of_households Australia 137488.46 54 null null null Austria 9921.48 16 310128.7 80282 0.0 Bahrain 548.4 2 null null null Belgium 39386.43 93 375967.8 89225 15.4 Brazil 1143.6 1 null null null Canada 3666.38 6 null null null Channel Islands 20086.91 25 null null null Cyprus 11999.56 15 19803.0 6215 5.0 Czech Republic 826.74 2 165202.2 45785 11.6 Denmark 17673.84 17 247879.9 53038 8.3 EIRE 256732.02 245 null null null European Community 1300.25 4 null null null Finland 21653.28 40 197998.0 49192 8.5 France 199407.74 368 2058369.0 525660 15.6 Germany 213626.0 427 2693560.0 686368 0.0 Greece 4760.52 5 203308.2 66351 1.0 Iceland 3598.21 6 10934.3 2639 null Israel 7221.69 5 null null null Italy 16671.74 36 1648755.8 501985 10.9 Japan 29711.3 16 null null null Lebanon 1693.88 1 null null null Malta 2725.59 5 6924.6 2458 0.0 Netherlands 276661.86 92 650359.0 134481 14.7 Norway 32378.32 34 358339.5 68781 null Poland 7086.49 18 379860.0 139811 3.2 Portugal 30999.92 51 176096.2 58408 8.8 RSA 1002.31 1 null null null Saudi Arabia 145.92 1 null null null Singapore 21279.29 7 null null null Spain 59733.38 86 1063763.0 271282 10.0 Sweden 34544.03 34 412844.7 89830 14.3 Switzerland 55139.03 49 520201.4 null null USA 3580.39 5 null null null United Arab Emirates 1902.28 3 null null null United Kingdom 6809729.7 15358 1912869.3 494924 9.9 Unspecified 2667.07 8 null null null

In [0]:
retail_pordata_1=(spark.sql("select country, AmountSpent, Orders, coalesce(GDP,0) as GDP, coalesce(Total_Goods,0) as Total_Goods, coalesce(Savings_rate_of_households,0) as Savings_rate_of_households from retail_pordata WHERE NOT(GDP IS NULL AND Total_Goods IS NULL AND Savings_rate_of_households IS NULL)"))
retail_pordata_1.createOrReplaceTempView("retail_pordata_1")
display(retail_pordata_1)

country AmountSpent Orders GDP Total_Goods Savings_rate_of_households Austria 9921.48 16 310128.7 80282 0.0 Belgium 39386.43 93 375967.8 89225 15.4 Cyprus 11999.56 15 19803.0 6215 5.0 Czech Republic 826.74 2 165202.2 45785 11.6 Denmark 17673.84 17 247879.9 53038 8.3 Finland 21653.28 40 197998.0 49192 8.5 France 199407.74 368 2058369.0 525660 15.6 Germany 213626.0 427 2693560.0 686368 0.0 Greece 4760.52 5 203308.2 66351 1.0 Iceland 3598.21 6 10934.3 2639 0.0 Italy 16671.74 36 1648755.8 501985 10.9 Malta 2725.59 5 6924.6 2458 0.0 Netherlands 276661.86 92 650359.0 134481 14.7 Norway 32378.32 34 358339.5 68781 0.0 Poland 7086.49 18 379860.0 139811 3.2 Portugal 30999.92 51 176096.2 58408 8.8 Spain 59733.38 86 1063763.0 271282 10.0 Sweden 34544.03 34 412844.7 89830 14.3 Switzerland 55139.03 49 520201.4 0 0.0 United Kingdom 6809729.7 15358 1912869.3 494924 9.9

In [0]:
display(retail_pordata_1)

country AmountSpent Orders GDP Total_Goods Savings_rate_of_households Austria 9921.48 16 310128.7 80282 0.0 Belgium 39386.43 93 375967.8 89225 15.4 Cyprus 11999.56 15 19803.0 6215 5.0 Czech Republic 826.74 2 165202.2 45785 11.6 Denmark 17673.84 17 247879.9 53038 8.3 Finland 21653.28 40 197998.0 49192 8.5 France 199407.74 368 2058369.0 525660 15.6 Germany 213626.0 427 2693560.0 686368 0.0 Greece 4760.52 5 203308.2 66351 1.0 Iceland 3598.21 6 10934.3 2639 0.0 Italy 16671.74 36 1648755.8 501985 10.9 Malta 2725.59 5 6924.6 2458 0.0 Netherlands 276661.86 92 650359.0 134481 14.7 Norway 32378.32 34 358339.5 68781 0.0 Poland 7086.49 18 379860.0 139811 3.2 Portugal 30999.92 51 176096.2 58408 8.8 Spain 59733.38 86 1063763.0 271282 10.0 Sweden 34544.03 34 412844.7 89830 14.3 Switzerland 55139.03 49 520201.4 0 0.0 United Kingdom 6809729.7 15358 1912869.3 494924 9.9

In [0]:
retail_pordata_2=(spark.sql("select * from retail_pordata_1 order by 2 DESC limit 3"))
retail_pordata_2.createOrReplaceTempView("retail_pordata_2")
display(retail_pordata_2)

country AmountSpent Orders GDP Total_Goods Savings_rate_of_households United Kingdom 6809729.7 15358 1912869.3 494924 9.9 Netherlands 276661.86 92 650359.0 134481 14.7 Germany 213626.0 427 2693560.0 686368 0.0

In [0]:
retail_pordata_3=(spark.sql("select * from retail_pordata_1 order by 2 ASC limit 3"))
retail_pordata_3.createOrReplaceTempView("retail_pordata_3")
display(retail_pordata_3)

country AmountSpent Orders GDP Total_Goods Savings_rate_of_households Czech Republic 826.74 2 165202.2 45785 11.6 Malta 2725.59 5 6924.6 2458 0.0 Iceland 3598.21 6 10934.3 2639 0.0

#### <span style="color:purple"> **Good luck and I hope you enjoyed doing this assignment :) !!!** </span>

<span style="color:red"> **Don't forget to submit your exam in a folder containing both your outputs PDF and your notebook. Once again, comment your code and don't forget to name the .zip file and notebook with your student numbers :) </span>